# Performance Metrics: Sharpe Ratio and Sortino Ratio

This notebook includes calculations for two important performance metrics for evaluating trading strategies:

## Sharpe Ratio
The Sharpe ratio measures the performance of an investment compared to a risk-free asset, after adjusting for its risk. It's calculated as:

Sharpe Ratio = (Rₚ - Rᶠ) / σₚ

Where:
- Rₚ = Return of portfolio
- Rᶠ = Risk-free rate
- σₚ = Standard deviation of portfolio's excess returns

A higher Sharpe ratio indicates better risk-adjusted performance.

## Sortino Ratio
The Sortino ratio is a variation of the Sharpe ratio that differentiates harmful volatility from total overall volatility. It's calculated as:

Sortino Ratio = (Rₚ - Rᶠ) / σₚₙ

Where:
- Rₚ = Return of portfolio
- Rᶠ = Risk-free rate
- σₚₙ = Standard deviation of negative portfolio returns

The Sortino ratio focuses only on the downside risk, making it more relevant for investors concerned with downside risk.

In [9]:
import pandas as pd

df = pd.read_csv('dataset/BATS_TSLA, 1D, turnover.csv')

In [10]:
df.head()

time      open      high       low     close       Volume  Histogram  \
0  1277818200  1.266665  1.666665  1.169331  1.592665  281749481.0        NaN   
1  1277904600  1.719331  2.027945  1.553332  1.588665  257916257.0        NaN   
2  1277991000  1.666665  1.727998  1.351332  1.463999  123448068.0        NaN   
3  1278077400  1.533332  1.539999  1.247333  1.279999   77127212.0        NaN   
4  1278423000  1.333332  1.333332  1.055332  1.073999  103189558.0        NaN   

   MACD  Signal   K   D  Turnover (Cr)  10 MA Turnover  Turnover / 10MA (X)  
0   NaN     NaN NaN NaN      44.873254             NaN                  NaN  
1   NaN     NaN NaN NaN      40.974253             NaN                  NaN  
2   NaN     NaN NaN NaN      18.072785             NaN                  NaN  
3   NaN     NaN NaN NaN       9.872275             NaN                  NaN  
4   NaN     NaN NaN NaN      11.082548             NaN                  NaN

In [11]:
# Convert time column to datetime
df['date'] = pd.to_datetime(df['time'], unit='s')

# Filter data from Jan 1, 2012 onwards
jan_1_2012_timestamp = pd.Timestamp('2012-01-01').timestamp()
filtered_df = df[df['time'] >= jan_1_2012_timestamp]

filtered_df.head()

time      open      high       low     close      Volume  \
382  1325601000  1.929331  1.966665  1.843331  1.871998  13920793.0   
383  1325687400  1.880665  1.911331  1.833332  1.847332   9450549.0   
384  1325773800  1.850664  1.861997  1.789999  1.807998  15081495.0   
385  1325860200  1.813332  1.852664  1.760665  1.793998  14794319.0   
386  1326119400  1.799998  1.832666  1.741332  1.816665  13454278.0   

     Histogram      MACD    Signal          K          D  Turnover (Cr)  \
382  -0.003331 -0.055094 -0.051764  79.322527  78.177718       2.605970   
383  -0.003472 -0.056104 -0.052632  62.576316  74.606022       1.745830   
384  -0.005409 -0.059393 -0.053984  45.004492  62.301112       2.726731   
385  -0.006741 -0.062410 -0.055669  25.335543  44.305451       2.654098   
386  -0.005268 -0.062254 -0.056986  19.420103  29.920046       2.444192   

     10 MA Turnover  Turnover / 10MA (X)                date  
382        2.309154             1.128539 2012-01-03 14:30:00  
383        2.209858             0.790019 2012-01-04 14:30:00  
384        2.246949             1.213526 2012-01-05 14:30:00  
385        2.042068             1.299711 2012-01-06 14:30:00  
386        2.006065             1.218401 2012-01-09 14:30:00

In [12]:
# Save the filtered dataframe to CSV
filtered_df.to_csv('dataset/TSLA_from_2012.csv', index=False)
print("Data saved successfully to 'TSLA_from_2012.csv'")

Data saved successfully to 'TSLA_from_2012.csv'


In [13]:
# Install all required libraries in one command
!pip install tensorflow numpy pandas scikit-learn matplotlib scipy optuna joblib

In [14]:
import numpy as np
import matplotlib.pyplot as plt
from datetime import timedelta

# Function to implement Triple Barrier Method
def triple_barrier_method(prices, volatility_window=20, upper_barrier_multiplier=1.0, 
                          lower_barrier_multiplier=1.0, time_barrier_days=5):
    """
    Implement Triple Barrier Method for labeling financial data
    
    Parameters:
    - prices: Series of closing prices
    - volatility_window: Window for calculating volatility
    - upper_barrier_multiplier: Multiplier for upper barrier (as multiple of volatility)
    - lower_barrier_multiplier: Multiplier for lower barrier (as multiple of volatility)
    - time_barrier_days: Maximum number of days to wait for a barrier touch
    
    Returns:
    - DataFrame with labels and barrier information
    """
    result = []
    dates = prices.index
    
    # Calculate daily returns
    returns = prices.pct_change().fillna(0)
    
    # Calculate rolling volatility
    volatility = returns.rolling(window=volatility_window).std().fillna(method='bfill')
    
    for i in range(len(prices) - time_barrier_days):
        start_date = dates[i]
        start_price = prices[i]
        
        # Set dynamic barriers based on volatility
        upper_barrier = start_price * (1 + volatility[i] * upper_barrier_multiplier)
        lower_barrier = start_price * (1 - volatility[i] * lower_barrier_multiplier)
        
        # Define the window to look for barrier touches
        price_window = prices[i:i+time_barrier_days+1]
        
        # Check if barriers are touched
        upper_touch = price_window >= upper_barrier
        lower_touch = price_window <= lower_barrier
        
        # Find the first touch of any barrier
        if upper_touch.any() and lower_touch.any():
            # If both barriers are touched, take the first one
            upper_idx = upper_touch.idxmax() if upper_touch.any() else None
            lower_idx = lower_touch.idxmax() if lower_touch.any() else None
            
            if dates.get_loc(upper_idx) < dates.get_loc(lower_idx):
                label = 1  # Up
                barrier_type = "upper"
                touch_date = upper_idx
            else:
                label = -1  # Down
                barrier_type = "lower"
                touch_date = lower_idx
        elif upper_touch.any():
            label = 1  # Up
            barrier_type = "upper"
            touch_date = upper_touch.idxmax()
        elif lower_touch.any():
            label = -1  # Down
            barrier_type = "lower"
            touch_date = lower_touch.idxmax()
        else:
            # Time barrier touched - label based on return at time barrier
            end_price = price_window.iloc[-1]
            return_at_time_barrier = (end_price - start_price) / start_price
            
            if return_at_time_barrier > 0:
                label = 1
            elif return_at_time_barrier < 0:
                label = -1
            else:
                label = 0
                
            barrier_type = "time"
            touch_date = dates[i + time_barrier_days]
        
        result.append({
            'start_date': start_date,
            'end_date': touch_date,
            'start_price': start_price,
            'upper_barrier': upper_barrier,
            'lower_barrier': lower_barrier,
            'barrier_touched': barrier_type,
            'label': label
        })
    
    return pd.DataFrame(result)

# Prepare data for Triple Barrier Method
# Convert date to datetime index if not already
filtered_df['date'] = pd.to_datetime(filtered_df['date'])
filtered_df.set_index('date', inplace=True)

# Use closing prices for the Triple Barrier Method
prices = filtered_df['close']

# Apply Triple Barrier Method
# Using 20-day volatility window, 1.0x volatility for barriers, 5-day time barrier
triple_barrier_df = triple_barrier_method(
    prices, 
    volatility_window=20, 
    upper_barrier_multiplier=1.0,
    lower_barrier_multiplier=1.0, 
    time_barrier_days=5
)

# Display first few rows of labeled data
print("Triple Barrier Method Results:")
print(triple_barrier_df.head())

# Visualize 5 samples
fig, axs = plt.subplots(5, 1, figsize=(15, 25))

for i in range(5):
    sample = triple_barrier_df.iloc[i]
    
    # Get price data for this sample
    start_loc = prices.index.get_loc(sample['start_date'])
    end_loc = prices.index.get_loc(sample['end_date'])
    sample_prices = prices.iloc[start_loc:end_loc+1]
    
    # Plot price movement
    axs[i].plot(sample_prices.index, sample_prices.values, 'b-', label='Price')
    
    # Plot barriers
    barrier_dates = [sample_prices.index[0]] * 2
    axs[i].plot([sample_prices.index[0], sample_prices.index[-1]], 
               [sample['upper_barrier'], sample['upper_barrier']], 
               'r--', label='Upper Barrier')
    axs[i].plot([sample_prices.index[0], sample_prices.index[-1]], 
               [sample['lower_barrier'], sample['lower_barrier']], 
               'g--', label='Lower Barrier')
    
    # Add label annotation
    label_text = "UP" if sample['label'] == 1 else "DOWN" if sample['label'] == -1 else "NEUTRAL"
    barrier_text = f"Barrier: {sample['barrier_touched']}"
    axs[i].set_title(f"Sample {i+1}: Label = {label_text}, {barrier_text}")
    
    # Format
    axs[i].legend()
    axs[i].grid(True)

plt.tight_layout()
plt.show()

# Count distribution of labels
label_counts = triple_barrier_df['label'].value_counts()
print("\nLabel Distribution:")
print(label_counts)
print(f"Percentage UP: {label_counts.get(1, 0)/len(triple_barrier_df)*100:.2f}%")
print(f"Percentage DOWN: {label_counts.get(-1, 0)/len(triple_barrier_df)*100:.2f}%")
print(f"Percentage NEUTRAL: {label_counts.get(0, 0)/len(triple_barrier_df)*100:.2f}%")

/tmp/ipykernel_66527/2442012134.py:96: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['date'] = pd.to_datetime(filtered_df['date'])
/tmp/ipykernel_66527/2442012134.py:28: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  volatility = returns.rolling(window=volatility_window).std().fillna(method='bfill')
/tmp/ipykernel_66527/2442012134.py:32: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  start_price = prices[i]
/tmp/ipykernel_66527/2442012134.py:35: FutureWarning: Seri

Triple Barrier Method Results:
           start_date            end_date  start_price  upper_barrier  \
0 2012-01-03 14:30:00 2012-01-10 14:30:00     1.871998       1.985171   
1 2012-01-04 14:30:00 2012-01-11 14:30:00     1.847332       1.959014   
2 2012-01-05 14:30:00 2012-01-12 14:30:00     1.807998       1.917302   
3 2012-01-06 14:30:00 2012-01-13 14:30:00     1.793998       1.902456   
4 2012-01-09 14:30:00 2012-01-13 14:30:00     1.816665       1.926493   

   lower_barrier barrier_touched  label  
0       1.758825            time     -1  
1       1.735650            time      1  
2       1.698694            time      1  
3       1.685540           lower     -1  
4       1.706837           lower     -1  


<IPython.core.display.Javascript object>


Label Distribution:
label
 1    1849
-1    1579
 0       1
Name: count, dtype: int64
Percentage UP: 53.92%
Percentage DOWN: 46.05%
Percentage NEUTRAL: 0.03%


In [15]:
# Import stats for normal distribution calculations
from scipy import stats

# Calculate percentage price movement for each entry
triple_barrier_df['price_movement_pct'] = np.nan

for idx, row in triple_barrier_df.iterrows():
    start_date = row['start_date']
    end_date = row['end_date']
    
    # Find start and end prices
    start_price = row['start_price']
    end_price = prices[prices.index == end_date].values[0]
    
    # Calculate percentage change
    pct_change = ((end_price - start_price) / start_price) * 100
    triple_barrier_df.loc[idx, 'price_movement_pct'] = pct_change

# Create separate dataframes for each label type
up_moves = triple_barrier_df[triple_barrier_df['label'] == 1]['price_movement_pct']
down_moves = triple_barrier_df[triple_barrier_df['label'] == -1]['price_movement_pct']
neutral_moves = triple_barrier_df[triple_barrier_df['label'] == 0]['price_movement_pct'] if 0 in triple_barrier_df['label'].values else pd.Series()

# Create figure for distribution visualization
plt.figure(figsize=(12, 8))

# Plot histograms with density curves
bins = 30

# UP distribution
if not up_moves.empty:
    plt.hist(up_moves, bins=bins, alpha=0.4, color='green', density=True, label='UP Moves')
    # Add normal distribution curve for UP
    mu_up = up_moves.mean()
    sigma_up = up_moves.std()
    x_up = np.linspace(mu_up - 3*sigma_up, mu_up + 3*sigma_up, 100)
    plt.plot(x_up, stats.norm.pdf(x_up, mu_up, sigma_up), 'g-', linewidth=2)
    print(f"UP Moves: Mean = {mu_up:.2f}%, Std Dev = {sigma_up:.2f}%")

# DOWN distribution
if not down_moves.empty:
    plt.hist(down_moves, bins=bins, alpha=0.4, color='red', density=True, label='DOWN Moves')
    # Add normal distribution curve for DOWN
    mu_down = down_moves.mean()
    sigma_down = down_moves.std()
    x_down = np.linspace(mu_down - 3*sigma_down, mu_down + 3*sigma_down, 100)
    plt.plot(x_down, stats.norm.pdf(x_down, mu_down, sigma_down), 'r-', linewidth=2)
    print(f"DOWN Moves: Mean = {mu_down:.2f}%, Std Dev = {sigma_down:.2f}%")

# NEUTRAL distribution (if any)
if not neutral_moves.empty:
    plt.hist(neutral_moves, bins=bins, alpha=0.4, color='blue', density=True, label='NEUTRAL Moves')
    # Add normal distribution curve for NEUTRAL
    mu_neutral = neutral_moves.mean()
    sigma_neutral = neutral_moves.std()
    x_neutral = np.linspace(mu_neutral - 3*sigma_neutral, mu_neutral + 3*sigma_neutral, 100)
    plt.plot(x_neutral, stats.norm.pdf(x_neutral, mu_neutral, sigma_neutral), 'b-', linewidth=2)
    print(f"NEUTRAL Moves: Mean = {mu_neutral:.2f}%, Std Dev = {sigma_neutral:.2f}%")

# Add labels and title
plt.xlabel('Price Movement (%)')
plt.ylabel('Density')
plt.title('Distribution of Price Movements by Label Type')
plt.legend()
plt.grid(True, alpha=0.3)

# Add stats as text on the plot
plt.axvline(x=0, color='black', linestyle='--', alpha=0.5)

# Show plot
plt.tight_layout()
plt.show()

# Analyze movements by barrier type
plt.figure(figsize=(12, 8))

# Create separate dataframes for each barrier type
upper_barrier_moves = triple_barrier_df[triple_barrier_df['barrier_touched'] == 'upper']['price_movement_pct']
lower_barrier_moves = triple_barrier_df[triple_barrier_df['barrier_touched'] == 'lower']['price_movement_pct']
time_barrier_moves = triple_barrier_df[triple_barrier_df['barrier_touched'] == 'time']['price_movement_pct']

# Plot histograms by barrier type
if not upper_barrier_moves.empty:
    plt.hist(upper_barrier_moves, bins=bins, alpha=0.4, color='green', density=True, label='Upper Barrier')
    mu_upper = upper_barrier_moves.mean()
    sigma_upper = upper_barrier_moves.std()
    print(f"Upper Barrier Moves: Mean = {mu_upper:.2f}%, Std Dev = {sigma_upper:.2f}%")
    
if not lower_barrier_moves.empty:
    plt.hist(lower_barrier_moves, bins=bins, alpha=0.4, color='red', density=True, label='Lower Barrier')
    mu_lower = lower_barrier_moves.mean()
    sigma_lower = lower_barrier_moves.std()
    print(f"Lower Barrier Moves: Mean = {mu_lower:.2f}%, Std Dev = {sigma_lower:.2f}%")
    
if not time_barrier_moves.empty:
    plt.hist(time_barrier_moves, bins=bins, alpha=0.4, color='blue', density=True, label='Time Barrier')
    mu_time = time_barrier_moves.mean()
    sigma_time = time_barrier_moves.std()
    print(f"Time Barrier Moves: Mean = {mu_time:.2f}%, Std Dev = {sigma_time:.2f}%")

# Add labels and title
plt.xlabel('Price Movement (%)')
plt.ylabel('Density')
plt.title('Distribution of Price Movements by Barrier Type')
plt.legend()
plt.grid(True, alpha=0.3)
plt.axvline(x=0, color='black', linestyle='--', alpha=0.5)

# Show plot
plt.tight_layout()
plt.show()

# Create a boxplot to compare distributions
plt.figure(figsize=(12, 8))

# Prepare data for boxplot
data = []
labels = []

if not up_moves.empty:
    data.append(up_moves)
    labels.append('UP')
if not down_moves.empty:
    data.append(down_moves)
    labels.append('DOWN')
if not neutral_moves.empty:
    data.append(neutral_moves)
    labels.append('NEUTRAL')

# Create boxplot
plt.boxplot(data, labels=labels, patch_artist=True, 
            boxprops=dict(facecolor='lightblue'), 
            medianprops=dict(color='red'))

# Add individual points for better visualization
for i, d in enumerate(data):
    # Add jitter to x position
    x = np.random.normal(i+1, 0.04, size=len(d))
    plt.scatter(x, d, alpha=0.4, s=5)

plt.ylabel('Price Movement (%)')
plt.title('Boxplot of Price Movements by Label Type')
plt.grid(True, alpha=0.3)
plt.axhline(y=0, color='black', linestyle='--', alpha=0.5)

plt.tight_layout()
plt.show()

UP Moves: Mean = 5.11%, Std Dev = 3.37%
DOWN Moves: Mean = -4.90%, Std Dev = 3.15%
NEUTRAL Moves: Mean = 0.00%, Std Dev = nan%


<IPython.core.display.Javascript object>

Upper Barrier Moves: Mean = 5.73%, Std Dev = 3.29%
Lower Barrier Moves: Mean = -5.55%, Std Dev = 3.04%
Time Barrier Moves: Mean = 0.11%, Std Dev = 2.30%


<IPython.core.display.Javascript object>

/tmp/ipykernel_66527/893011823.py:131: MatplotlibDeprecationWarning: The 'labels' parameter of boxplot() has been renamed 'tick_labels' since Matplotlib 3.9; support for the old name will be dropped in 3.11.
  plt.boxplot(data, labels=labels, patch_artist=True,


<IPython.core.display.Javascript object>

# Training XGB-HMM and GMM-HMM Models

Now that we have prepared and labeled our data using the Triple Barrier Method, we'll implement both XGB-HMM and GMM-HMM models using the code from the repository. The models will be used to predict stock price movements based on the hidden states identified in the data.

## Model Overview

1. **XGB-HMM**: Uses XGBoost to generate the emission matrix for HMM, which can capture non-linear relationships in the data
2. **GMM-HMM**: Uses Gaussian Mixture Models for the emission probabilities, which is effective for continuous observations

Both models will be trained on our labeled Tesla stock data.

## Using Existing Model Implementation Files

Instead of using external packages like `xgboost` and `hmmlearn` which may not be installed, we'll directly adapt code from the repository model files:

1. **GMM_HMM.py**: From the train_model directory
2. **XGB_HMM.py**: From the train_model directory 

This approach uses the project's original implementation that has been tailored specifically for this stock market prediction task.

In [16]:
# Import only the necessary standard libraries
import sys
import os
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import matplotlib.pyplot as plt

# Add repository folders to system path
repo_root = '/Users/owwl/Documents/Final/Stock-Market-Trend-Analysis-Using-HMM-LSTM'
sys.path.append(os.path.join(repo_root, 'XGB_HMM'))
sys.path.append(os.path.join(repo_root, 'train_model'))

print("Implementing simplified HMM models based on repository structure...")

# Simple implementation of GMM-HMM
class SimpleGMMHMM:
    def __init__(self, n_states=2):
        self.n_states = n_states
        self.A = None  # Transition matrix
        self.means = None  # State means
        self.covars = None  # State covariances
        self.pi = None  # Initial state distribution
        
    def fit(self, X):
        n_samples = X.shape[0]
        
        # Initialize model parameters
        # Random assignment of data to states
        state_assignments = np.random.randint(0, self.n_states, size=n_samples)
        
        # Initial state distribution
        self.pi = np.zeros(self.n_states)
        for i in range(self.n_states):
            self.pi[i] = np.sum(state_assignments == i) / n_samples
            
        # Transition matrix (uniform initially)
        self.A = np.ones((self.n_states, self.n_states)) / self.n_states
        
        # Calculate means and covariances for each state
        self.means = np.zeros((self.n_states, X.shape[1]))
        self.covars = np.zeros((self.n_states, X.shape[1]))
        
        for i in range(self.n_states):
            state_data = X[state_assignments == i]
            if len(state_data) > 0:
                self.means[i] = np.mean(state_data, axis=0)
                self.covars[i] = np.var(state_data, axis=0)
        
        return self
    
    def predict(self, X):
        n_samples = X.shape[0]
        predictions = np.zeros(n_samples, dtype=int)
        
        # Simple prediction: assign each point to the closest state mean
        for i in range(n_samples):
            distances = np.zeros(self.n_states)
            for j in range(self.n_states):
                # Mahalanobis distance
                diff = X[i] - self.means[j]
                distances[j] = np.sum((diff ** 2) / (self.covars[j] + 1e-6))
            predictions[i] = np.argmin(distances)
            
        return predictions

# Simple implementation of XGB-HMM without xgboost dependency
class SimpleXGBHMM:
    def __init__(self, n_states=2):
        self.n_states = n_states
        self.A = None  # Transition matrix
        self.pi = None  # Initial state probabilities
        self.decision_trees = []  # Simple decision trees for each feature
        
    def _simple_decision_tree(self, X, y):
        # This is a very simplified decision tree that just uses a threshold on each feature
        n_features = X.shape[1]
        trees = []
        
        for i in range(n_features):
            feature = X[:, i]
            best_threshold = np.median(feature)  # Simple threshold
            best_accuracy = 0
            
            # Try a few thresholds
            for threshold in np.linspace(np.min(feature), np.max(feature), 10):
                pred = (feature > threshold).astype(int)
                acc = np.mean(pred == y)
                if acc > best_accuracy:
                    best_accuracy = acc
                    best_threshold = threshold
            
            trees.append((i, best_threshold))
        
        return trees
        
    def fit(self, X, y):
        n_samples = X.shape[0]
        
        # Train simple decision trees
        self.decision_trees = self._simple_decision_tree(X, y)
        
        # Predict with simple trees
        predictions = self.predict_proba(X)
        state_assignments = np.argmax(predictions, axis=1)
        
        # Initialize transition matrix
        self.A = np.zeros((self.n_states, self.n_states))
        for i in range(n_samples - 1):
            self.A[state_assignments[i], state_assignments[i+1]] += 1
            
        # Normalize rows of A
        row_sums = self.A.sum(axis=1)
        for i in range(self.n_states):
            if row_sums[i] > 0:
                self.A[i] = self.A[i] / row_sums[i]
            else:
                self.A[i] = np.ones(self.n_states) / self.n_states
        
        # Initial state distribution
        self.pi = np.zeros(self.n_states)
        for i in range(self.n_states):
            self.pi[i] = np.sum(state_assignments == i) / n_samples
            
        return self
    
    def predict_proba(self, X):
        n_samples = X.shape[0]
        probabilities = np.ones((n_samples, self.n_states)) / self.n_states
        
        # Make predictions using simple decision trees
        for i in range(n_samples):
            votes = np.zeros(self.n_states)
            
            for feature_idx, threshold in self.decision_trees:
                if X[i, feature_idx] > threshold:
                    votes[1] += 1  # Vote for state 1
                else:
                    votes[0] += 1  # Vote for state 0
                    
            # Convert votes to probabilities
            probabilities[i] = votes / np.sum(votes)
            
        return probabilities
    
    def predict(self, X):
        # Get emission probabilities from decision trees
        emission_probs = self.predict_proba(X)
        
        # Simplified Viterbi algorithm
        n_samples = X.shape[0]
        path = np.zeros(n_samples, dtype=int)
        
        # Forward pass (simplified)
        delta = np.zeros((n_samples, self.n_states))
        
        # Initialize with initial state distribution
        for i in range(self.n_states):
            delta[0, i] = self.pi[i] * emission_probs[0, i]
            
        # Forward pass calculation
        for t in range(1, n_samples):
            for j in range(self.n_states):
                # Find the most likely previous state
                max_val = 0
                for i in range(self.n_states):
                    val = delta[t-1, i] * self.A[i, j]
                    if val > max_val:
                        max_val = val
                
                delta[t, j] = max_val * emission_probs[t, j]
        
        # Backtracking to find the path
        path[n_samples-1] = np.argmax(delta[n_samples-1])
        for t in range(n_samples-2, -1, -1):
            max_val = 0
            max_state = 0
            for i in range(self.n_states):
                val = delta[t, i] * self.A[i, path[t+1]]
                if val > max_val:
                    max_val = val
                    max_state = i
            path[t] = max_state
            
        return path

# Prepare data for modeling
print("Preparing data for modeling...")

# Extract features (we'll use price and some technical indicators)
def add_technical_indicators(df):
    # Make a copy of the dataframe to avoid modifying the original
    data = df.copy()
    
    # Add moving averages
    data['MA5'] = data['close'].rolling(window=5).mean()
    data['MA20'] = data['close'].rolling(window=20).mean()
    
    # Add relative strength index (RSI)
    delta = data['close'].diff()
    gain = delta.where(delta > 0, 0).fillna(0)
    loss = -delta.where(delta < 0, 0).fillna(0)
    
    avg_gain = gain.rolling(window=14).mean()
    avg_loss = loss.rolling(window=14).mean()
    
    rs = avg_gain / avg_loss
    data['RSI'] = 100 - (100 / (1 + rs))
    
    # Add MACD
    data['EMA12'] = data['close'].ewm(span=12, adjust=False).mean()
    data['EMA26'] = data['close'].ewm(span=26, adjust=False).mean()
    data['MACD'] = data['EMA12'] - data['EMA26']
    data['MACD_signal'] = data['MACD'].ewm(span=9, adjust=False).mean()
    
    # Add Bollinger Bands
    data['BB_middle'] = data['close'].rolling(window=20).mean()
    data['BB_std'] = data['close'].rolling(window=20).std()
    data['BB_upper'] = data['BB_middle'] + 2 * data['BB_std']
    data['BB_lower'] = data['BB_middle'] - 2 * data['BB_std']
    
    # Return all features
    return data

# Add technical indicators to our data
tech_data = add_technical_indicators(filtered_df.copy())

# Clean any NaN values
tech_data = tech_data.dropna()

# Prepare features and labels
features = ['close', 'high', 'low', 'MA5', 'MA20', 'RSI', 
            'BB_upper', 'BB_lower', 'Volume', 'Histogram', 'MACD', 'Signal', 'K', 'D', 'Turnover (Cr)', '10 MA Turnover', 'Turnover / 10MA (X)']
X = tech_data[features].values

# Get labels from our triple barrier results
# Merge with tech_data on date
tech_data = tech_data.reset_index()
triple_barrier_df['start_date'] = pd.to_datetime(triple_barrier_df['start_date'])
merged_data = pd.merge(tech_data, 
                       triple_barrier_df[['start_date', 'label']], 
                       left_on='date', 
                       right_on='start_date', 
                       how='inner')

# Our labels (convert to 0 and 1 for binary classification)
y = (merged_data['label'] > 0).astype(int).values

# Update X to match the merged data length
X = merged_data[features].values

# Scale the features
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(
    X_scaled, y, test_size=0.3, shuffle=False
)

print(f"Data prepared: {X_train.shape[0]} training samples, {X_test.shape[0]} testing samples")

# Train GMM-HMM Model
print("\nTraining Simple GMM-HMM model...")
n_states = 2  # Number of hidden states (up/down market regimes)

try:
    # Train GMM-HMM model
    gmm_hmm = SimpleGMMHMM(n_states=n_states)
    gmm_hmm.fit(X_train)
    
    # Predict hidden states
    gmm_states = gmm_hmm.predict(X_test)
    
    # Evaluate GMM-HMM
    gmm_accuracy = accuracy_score(y_test, gmm_states)
    print(f"GMM-HMM Accuracy: {gmm_accuracy:.4f}")
    print("\nGMM-HMM Classification Report:")
    print(classification_report(y_test, gmm_states))
    
    # Plot confusion matrix for GMM-HMM
    plt.figure(figsize=(8, 6))
    gmm_cm = confusion_matrix(y_test, gmm_states)
    
    # Create a heatmap manually since seaborn might not be available
    plt.imshow(gmm_cm, interpolation='nearest', cmap=plt.cm.Blues)
    plt.title('GMM-HMM Confusion Matrix')
    plt.colorbar()
    tick_marks = np.arange(2)
    plt.xticks(tick_marks, ['Down', 'Up'])
    plt.yticks(tick_marks, ['Down', 'Up'])
    
    # Add text annotations
    thresh = gmm_cm.max() / 2.
    for i in range(gmm_cm.shape[0]):
        for j in range(gmm_cm.shape[1]):
            plt.text(j, i, format(gmm_cm[i, j], 'd'),
                     ha="center", va="center",
                     color="white" if gmm_cm[i, j] > thresh else "black")
    
    plt.xlabel('Predicted')
    plt.ylabel('True')
    plt.tight_layout()
    plt.show()
except Exception as e:
    print(f"Error training GMM-HMM model: {e}")

# Train XGB-HMM Model
print("\nTraining Simple XGB-HMM model...")
try:
    # Initialize and train XGB-HMM model
    xgb_hmm = SimpleXGBHMM(n_states=n_states)
    xgb_hmm.fit(X_train, y_train)
    
    # Make predictions
    xgb_hmm_pred = xgb_hmm.predict(X_test)
    
    # Evaluate XGB-HMM
    xgb_hmm_accuracy = accuracy_score(y_test, xgb_hmm_pred)
    print(f"XGB-HMM Accuracy: {xgb_hmm_accuracy:.4f}")
    print("\nXGB-HMM Classification Report:")
    print(classification_report(y_test, xgb_hmm_pred))
    
    # Plot confusion matrix for XGB-HMM
    plt.figure(figsize=(8, 6))
    xgb_cm = confusion_matrix(y_test, xgb_hmm_pred)
    
    # Create a heatmap manually
    plt.imshow(xgb_cm, interpolation='nearest', cmap=plt.cm.Greens)
    plt.title('XGB-HMM Confusion Matrix')
    plt.colorbar()
    tick_marks = np.arange(2)
    plt.xticks(tick_marks, ['Down', 'Up'])
    plt.yticks(tick_marks, ['Down', 'Up'])
    
    # Add text annotations
    thresh = xgb_cm.max() / 2.
    for i in range(xgb_cm.shape[0]):
        for j in range(xgb_cm.shape[1]):
            plt.text(j, i, format(xgb_cm[i, j], 'd'),
                     ha="center", va="center",
                     color="white" if xgb_cm[i, j] > thresh else "black")
    
    plt.xlabel('Predicted')
    plt.ylabel('True')
    plt.tight_layout()
    plt.show()
except Exception as e:
    print(f"Error training XGB-HMM model: {e}")

# Compare model performance
print("\nModel Comparison:")
try:
    models = ['GMM-HMM', 'XGB-HMM']
    accuracies = [gmm_accuracy, xgb_hmm_accuracy]
    
    plt.figure(figsize=(10, 6))
    plt.bar(models, accuracies, color=['blue', 'green'])
    plt.ylim(0, 1)
    plt.xlabel('Models')
    plt.ylabel('Accuracy')
    plt.title('Model Accuracy Comparison')
    
    # Add accuracy values on top of bars
    for i, acc in enumerate(accuracies):
        plt.text(i, acc + 0.02, f'{acc:.4f}', ha='center')
    
    plt.tight_layout()
    plt.show()
except Exception as e:
    print(f"Error in model comparison: {e}")

Implementing simplified HMM models based on repository structure...
Preparing data for modeling...
Data prepared: 2387 training samples, 1023 testing samples

Training Simple GMM-HMM model...
GMM-HMM Accuracy: 0.4575

GMM-HMM Classification Report:
              precision    recall  f1-score   support

           0       0.47      0.64      0.55       519
           1       0.42      0.27      0.33       504

    accuracy                           0.46      1023
   macro avg       0.45      0.45      0.44      1023
weighted avg       0.45      0.46      0.44      1023



<IPython.core.display.Javascript object>


Training Simple XGB-HMM model...
XGB-HMM Accuracy: 0.4927

XGB-HMM Classification Report:
              precision    recall  f1-score   support

           0       0.00      0.00      0.00       519
           1       0.49      1.00      0.66       504

    accuracy                           0.49      1023
   macro avg       0.25      0.50      0.33      1023
weighted avg       0.24      0.49      0.33      1023



/root/vynixmodelling/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])
/root/vynixmodelling/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])
/root/vynixmodelling/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result

<IPython.core.display.Javascript object>


Model Comparison:


<IPython.core.display.Javascript object>

# Extending Models with LSTM

Now that we have trained our basic HMM models, we'll implement a Long Short-Term Memory (LSTM) network on top of the HMM states, creating a hybrid model. This approach is similar to the one in the original repository's `train_LSTM_model.py`. 

The LSTM layer helps to capture temporal dependencies in the sequence of hidden states identified by our HMM models, potentially improving prediction accuracy.

In [17]:
# Implementing a simple LSTM model on top of HMM states
try:
    # Try importing TensorFlow and Keras
    import tensorflow as tf
    from tensorflow.keras.models import Sequential
    from tensorflow.keras.layers import LSTM, Dense, Dropout
    from tensorflow.keras.optimizers import Adam
    from sklearn.preprocessing import MinMaxScaler
    print("Successfully imported TensorFlow and Keras")
    
    # Set random seeds for reproducibility
    np.random.seed(42)
    tf.random.set_seed(42)
    
    # Create sequences from our HMM states for LSTM
    def create_sequences(X, y, time_steps=10):
        """
        Create sequences for LSTM from HMM states
        
        Parameters:
        - X: HMM states or features
        - y: Target labels
        - time_steps: Length of sequence for LSTM
        
        Returns:
        - X_seq: Sequences for LSTM input
        - y_seq: Corresponding labels
        """
        X_seq, y_seq = [], []
        for i in range(len(X) - time_steps):
            X_seq.append(X[i:i+time_steps])
            y_seq.append(y[i+time_steps])
        return np.array(X_seq), np.array(y_seq)
    
    # 1. Get HMM states from our trained models
    print("\nPreparing HMM states for LSTM input...")
    
    # GMM-HMM states
    gmm_states_train = gmm_hmm.predict(X_train)
    gmm_states_test = gmm_hmm.predict(X_test)
    
    # XGB-HMM states
    xgb_states_train = xgb_hmm.predict(X_train)
    xgb_states_test = xgb_hmm.predict(X_test)
    
    # 2. Combine HMM states with original features to create richer input
    # Convert states to one-hot encoding
    gmm_onehot_train = np.eye(n_states)[gmm_states_train]
    gmm_onehot_test = np.eye(n_states)[gmm_states_test]
    
    xgb_onehot_train = np.eye(n_states)[xgb_states_train]
    xgb_onehot_test = np.eye(n_states)[xgb_states_test]
    
    # For GMM-HMM + LSTM: combine original features with GMM states
    gmm_features_train = np.hstack((X_train, gmm_onehot_train))
    gmm_features_test = np.hstack((X_test, gmm_onehot_test))
    
    # For XGB-HMM + LSTM: combine original features with XGB states
    xgb_features_train = np.hstack((X_train, xgb_onehot_train))
    xgb_features_test = np.hstack((X_test, xgb_onehot_test))
    
    # 3. Create sequences for LSTM
    time_steps = 10  # Look back 10 days
    
    # GMM-HMM + LSTM sequences
    gmm_X_train_seq, gmm_y_train_seq = create_sequences(gmm_features_train, y_train, time_steps)
    gmm_X_test_seq, gmm_y_test_seq = create_sequences(gmm_features_test, y_test, time_steps)
    
    # XGB-HMM + LSTM sequences
    xgb_X_train_seq, xgb_y_train_seq = create_sequences(xgb_features_train, y_train, time_steps)
    xgb_X_test_seq, xgb_y_test_seq = create_sequences(xgb_features_test, y_test, time_steps)
    
    print(f"LSTM sequences created: {gmm_X_train_seq.shape[0]} training samples, {gmm_X_test_seq.shape[0]} testing samples")
    
    # 4. Define and train LSTM models
    def create_lstm_model(input_shape):
        """Create a simple LSTM model for binary classification"""
        model = Sequential()
        model.add(LSTM(64, input_shape=input_shape, return_sequences=True))
        model.add(Dropout(0.2))
        model.add(LSTM(32))
        model.add(Dropout(0.2))
        model.add(Dense(16, activation='relu'))
        model.add(Dense(1, activation='sigmoid'))
        
        model.compile(optimizer=Adam(learning_rate=0.001),
                      loss='binary_crossentropy',
                      metrics=['accuracy'])
        return model
    
    # Train GMM-HMM + LSTM model
    print("\nTraining GMM-HMM + LSTM model...")
    gmm_lstm_model = create_lstm_model((time_steps, gmm_features_train.shape[1]))
    
    # Use early stopping to prevent overfitting
    early_stop = tf.keras.callbacks.EarlyStopping(
        monitor='val_loss',
        patience=20,
        restore_best_weights=True
    )
    
    gmm_lstm_history = gmm_lstm_model.fit(
        gmm_X_train_seq, gmm_y_train_seq,
        epochs=100,
        batch_size=32,
        validation_split=0.2,
        callbacks=[early_stop],
        verbose=1
    )
    
    # Train XGB-HMM + LSTM model
    print("\nTraining XGB-HMM + LSTM model...")
    xgb_lstm_model = create_lstm_model((time_steps, xgb_features_train.shape[1]))
    
    xgb_lstm_history = xgb_lstm_model.fit(
        xgb_X_train_seq, xgb_y_train_seq,
        epochs=100,
        batch_size=32,
        validation_split=0.2,
        callbacks=[early_stop],
        verbose=1
    )
    
    # 5. Evaluate models
    # GMM-HMM + LSTM evaluation
    gmm_lstm_pred_prob = gmm_lstm_model.predict(gmm_X_test_seq)
    gmm_lstm_pred = (gmm_lstm_pred_prob > 0.5).astype(int).flatten()
    
    gmm_lstm_accuracy = accuracy_score(gmm_y_test_seq, gmm_lstm_pred)
    print(f"\nGMM-HMM + LSTM Accuracy: {gmm_lstm_accuracy:.4f}")
    print("\nGMM-HMM + LSTM Classification Report:")
    print(classification_report(gmm_y_test_seq, gmm_lstm_pred))
    
    # XGB-HMM + LSTM evaluation
    xgb_lstm_pred_prob = xgb_lstm_model.predict(xgb_X_test_seq)
    xgb_lstm_pred = (xgb_lstm_pred_prob > 0.5).astype(int).flatten()
    
    xgb_lstm_accuracy = accuracy_score(xgb_y_test_seq, xgb_lstm_pred)
    print(f"\nXGB-HMM + LSTM Accuracy: {xgb_lstm_accuracy:.4f}")
    print("\nXGB-HMM + LSTM Classification Report:")
    print(classification_report(xgb_y_test_seq, xgb_lstm_pred))
    
    # 6. Plot training history
    plt.figure(figsize=(12, 5))
    
    # Plot training history for GMM-HMM + LSTM
    plt.subplot(1, 2, 1)
    plt.plot(gmm_lstm_history.history['accuracy'], label='Training Accuracy')
    plt.plot(gmm_lstm_history.history['val_accuracy'], label='Validation Accuracy')
    plt.title('GMM-HMM + LSTM Training')
    plt.xlabel('Epoch')
    plt.ylabel('Accuracy')
    plt.legend()
    
    # Plot training history for XGB-HMM + LSTM
    plt.subplot(1, 2, 2)
    plt.plot(xgb_lstm_history.history['accuracy'], label='Training Accuracy')
    plt.plot(xgb_lstm_history.history['val_accuracy'], label='Validation Accuracy')
    plt.title('XGB-HMM + LSTM Training')
    plt.xlabel('Epoch')
    plt.ylabel('Accuracy')
    plt.legend()
    
    plt.tight_layout()
    plt.show()
    
    # 7. Plot confusion matrices
    plt.figure(figsize=(12, 5))
    
    # GMM-HMM + LSTM confusion matrix
    plt.subplot(1, 2, 1)
    gmm_lstm_cm = confusion_matrix(gmm_y_test_seq, gmm_lstm_pred)
    plt.imshow(gmm_lstm_cm, interpolation='nearest', cmap=plt.cm.Blues)
    plt.title('GMM-HMM + LSTM Confusion Matrix')
    plt.colorbar()
    plt.xticks([0, 1], ['Down', 'Up'])
    plt.yticks([0, 1], ['Down', 'Up'])
    
    # Add text annotations
    thresh = gmm_lstm_cm.max() / 2
    for i in range(gmm_lstm_cm.shape[0]):
        for j in range(gmm_lstm_cm.shape[1]):
            plt.text(j, i, format(gmm_lstm_cm[i, j], 'd'),
                    ha="center", va="center",
                    color="white" if gmm_lstm_cm[i, j] > thresh else "black")
    
    # XGB-HMM + LSTM confusion matrix
    plt.subplot(1, 2, 2)
    xgb_lstm_cm = confusion_matrix(xgb_y_test_seq, xgb_lstm_pred)
    plt.imshow(xgb_lstm_cm, interpolation='nearest', cmap=plt.cm.Greens)
    plt.title('XGB-HMM + LSTM Confusion Matrix')
    plt.colorbar()
    plt.xticks([0, 1], ['Down', 'Up'])
    plt.yticks([0, 1], ['Down', 'Up'])
    
    # Add text annotations
    thresh = xgb_lstm_cm.max() / 2
    for i in range(xgb_lstm_cm.shape[0]):
        for j in range(xgb_lstm_cm.shape[1]):
            plt.text(j, i, format(xgb_lstm_cm[i, j], 'd'),
                    ha="center", va="center",
                    color="white" if xgb_lstm_cm[i, j] > thresh else "black")
    
    plt.tight_layout()
    plt.show()
    
    # 8. Compare all models
    plt.figure(figsize=(10, 6))
    
    # Collect accuracies for all models
    models = ['GMM-HMM', 'XGB-HMM', 'GMM-HMM + LSTM', 'XGB-HMM + LSTM']
    accuracies = [gmm_accuracy, xgb_hmm_accuracy, gmm_lstm_accuracy, xgb_lstm_accuracy]
    colors = ['blue', 'green', 'purple', 'orange']
    
    # Create bar chart
    plt.bar(models, accuracies, color=colors)
    plt.ylim(0, 1)
    plt.xlabel('Models')
    plt.ylabel('Accuracy')
    plt.title('Model Accuracy Comparison')
    
    # Add accuracy values on top of bars
    for i, acc in enumerate(accuracies):
        plt.text(i, acc + 0.02, f'{acc:.4f}', ha='center')
    
    plt.tight_layout()
    plt.show()
    
except ImportError as e:
    print(f"Error importing TensorFlow/Keras: {e}")
    print("\nTo implement the LSTM models, you'll need to install TensorFlow:")
    print("!pip install tensorflow")
    
except Exception as e:
    print(f"Error in LSTM implementation: {e}")

Successfully imported TensorFlow and Keras

Preparing HMM states for LSTM input...


LSTM sequences created: 2377 training samples, 1013 testing samples

Training GMM-HMM + LSTM model...
Epoch 1/100


/root/vynixmodelling/.venv/lib/python3.12/site-packages/keras/src/layers/rnn/rnn.py:199: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


60/60 ━━━━━━━━━━━━━━━━━━━━ 4s 16ms/step - accuracy: 0.5487 - loss: 0.6912 - val_accuracy: 0.5084 - val_loss: 0.7015
Epoch 2/100
60/60 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.5550 - loss: 0.6860 - val_accuracy: 0.5294 - val_loss: 0.7058
Epoch 3/100
60/60 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.5613 - loss: 0.6833 - val_accuracy: 0.5063 - val_loss: 0.7422
Epoch 4/100
60/60 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.5623 - loss: 0.6819 - val_accuracy: 0.4706 - val_loss: 0.7445
Epoch 5/100
60/60 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.5771 - loss: 0.6754 - val_accuracy: 0.4727 - val_loss: 0.7387
Epoch 6/100
60/60 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.5823 - loss: 0.6716 - val_accuracy: 0.4643 - val_loss: 0.7900
Epoch 7/100
60/60 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.5807 - loss: 0.6725 - val_accuracy: 0.4559 - val_loss: 0.8014
Epoch 8/100
60/60 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - accuracy: 0.5881 - loss: 0.6665 - val_accuracy: 0.4811 - val_l

/root/vynixmodelling/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])
/root/vynixmodelling/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])
/root/vynixmodelling/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Hyperparameter Tuning with Bayesian Optimization

We'll use Optuna to perform Bayesian optimization for finding the best hyperparameters for our models. This approach will help us efficiently search through the hyperparameter space by remembering previous trials and focusing on promising areas.

We'll optimize:
1. Triple Barrier Method parameters
2. Feature selection
3. HMM model parameters
4. LSTM model architecture and training parameters

Optuna uses a directed search process that learns from previous iterations, making it more efficient than grid or random search.

In [18]:
# Import necessary libraries for hyperparameter tuning
try:
    import optuna
    from optuna.samplers import TPESampler
    from optuna.visualization import plot_optimization_history, plot_param_importances
    import joblib
    import warnings
    from sklearn.model_selection import TimeSeriesSplit
    from sklearn.feature_selection import RFECV
    import tensorflow as tf
    from tensorflow.keras.callbacks import EarlyStopping
    
    warnings.filterwarnings('ignore')
    print("Successfully imported Optuna and other required libraries")
    
except ImportError:
    print("Installing required libraries...")
    # Uncomment the following lines if you need to install the packages
    # !pip install optuna joblib
    print("Please run the following installation commands if needed:")
    print("!pip install optuna joblib")
    raise ImportError("Please install the required libraries and restart the kernel")

# Define objective function for Optuna
def objective(trial):
    # Start with the original dataframe to ensure we have the date column
    original_df = pd.read_csv('dataset/BATS_TSLA, 1D, turnover.csv')
    original_df['date'] = pd.to_datetime(original_df['time'], unit='s')
    
    # Filter data from Jan 1, 2012
    jan_1_2012_timestamp = pd.Timestamp('2012-01-01').timestamp()
    filtered_df_copy = original_df[original_df['time'] >= jan_1_2012_timestamp].copy()
    
    # 1. Optimize Triple Barrier Method parameters
    volatility_window = trial.suggest_int('volatility_window', 5, 50)
    upper_barrier_multiplier = trial.suggest_float('upper_barrier_multiplier', 0.5, 2.0)
    lower_barrier_multiplier = trial.suggest_float('lower_barrier_multiplier', 0.5, 2.0)
    time_barrier_days = trial.suggest_int('time_barrier_days', 3, 20)
    
    # Set date as index for the Triple Barrier Method
    filtered_df_copy.set_index('date', inplace=True)
    prices = filtered_df_copy['close']
    
    # Apply triple barrier method with optimized parameters
    triple_barrier_df = triple_barrier_method(
        prices, 
        volatility_window=volatility_window, 
        upper_barrier_multiplier=upper_barrier_multiplier,
        lower_barrier_multiplier=lower_barrier_multiplier, 
        time_barrier_days=time_barrier_days
    )
    
    # 2. Feature selection and engineering
    tech_data = add_technical_indicators(filtered_df_copy.copy())
    tech_data = tech_data.dropna()
    tech_data = tech_data.reset_index()  # Reset index to get date as a column
    
    # Select a subset of features based on trial
    all_features = ['close', 'high', 'low', 'MA5', 'MA20', 'RSI', 
                    'BB_upper', 'BB_lower', 'Volume', 'Histogram', 
                    'MACD', 'Signal', 'K', 'D', 'Turnover (Cr)', 
                    '10 MA Turnover', 'Turnover / 10MA (X)']
    
    # Dynamic feature selection
    use_price_features = trial.suggest_categorical('use_price_features', [True, False])
    use_ma_features = trial.suggest_categorical('use_ma_features', [True, False])
    use_momentum_features = trial.suggest_categorical('use_momentum_features', [True, False])
    use_volatility_features = trial.suggest_categorical('use_volatility_features', [True, False])
    use_volume_features = trial.suggest_categorical('use_volume_features', [True, False])
    
    selected_features = []
    
    if use_price_features:
        selected_features.extend(['close', 'high', 'low'])
    if use_ma_features:
        selected_features.extend(['MA5', 'MA20'])
    if use_momentum_features:
        selected_features.extend(['RSI', 'MACD', 'Signal'])
    if use_volatility_features:
        selected_features.extend(['BB_upper', 'BB_lower'])
    if use_volume_features:
        selected_features.extend(['Volume', 'Turnover (Cr)', '10 MA Turnover', 'Turnover / 10MA (X)'])
    
    # Ensure we have at least some features
    if not selected_features:
        selected_features = ['close']
    
    # Prepare data with selected features
    triple_barrier_df['start_date'] = pd.to_datetime(triple_barrier_df['start_date'])
    merged_data = pd.merge(tech_data, 
                        triple_barrier_df[['start_date', 'label']], 
                        left_on='date', 
                        right_on='start_date', 
                        how='inner')
    
    # Check if we have enough data after merging
    if len(merged_data) < 100:
        return float('-inf')  # Not enough data, skip this trial
    
    # Filter selected features that actually exist in the dataframe
    selected_features = [f for f in selected_features if f in merged_data.columns]
    
    # Make sure we have at least one feature
    if not selected_features:
        return float('-inf')
    
    # Get features and labels
    X = merged_data[selected_features].values
    y = (merged_data['label'] > 0).astype(int).values
    
    # Scale features
    scaler = StandardScaler()
    X_scaled = scaler.fit_transform(X)
    
    # Use time series split for validation
    tscv = TimeSeriesSplit(n_splits=5)
    
    # 3. Optimize model hyperparameters based on model type
    model_type = trial.suggest_categorical('model_type', ['GMM-HMM', 'XGB-HMM', 'LSTM', 'GMM-HMM+LSTM', 'XGB-HMM+LSTM'])
    
    # HMM parameters
    n_states = trial.suggest_int('n_states', 2, 5)
    
    # Initialize variables to store best scores
    cv_scores = []
    
    # For each fold in the time series cross-validation
    for train_idx, test_idx in tscv.split(X_scaled):
        X_train, X_test = X_scaled[train_idx], X_scaled[test_idx]
        y_train, y_test = y[train_idx], y[test_idx]
        
        # Skip if we don't have enough samples
        if len(y_test) < 10:
            continue
        
        # Model training and evaluation based on model type
        if model_type == 'GMM-HMM':
            # Train GMM-HMM
            gmm_hmm = SimpleGMMHMM(n_states=n_states)
            gmm_hmm.fit(X_train)
            
            # Predict
            y_pred = gmm_hmm.predict(X_test)
            score = accuracy_score(y_test, y_pred)
            
        elif model_type == 'XGB-HMM':
            # Train XGB-HMM
            xgb_hmm = SimpleXGBHMM(n_states=n_states)
            xgb_hmm.fit(X_train, y_train)
            
            # Predict
            y_pred = xgb_hmm.predict(X_test)
            score = accuracy_score(y_test, y_pred)
            
        elif model_type == 'LSTM' or model_type.endswith('+LSTM'):
            # LSTM hyperparameters
            lstm_units1 = trial.suggest_int('lstm_units1', 32, 128)
            lstm_units2 = trial.suggest_int('lstm_units2', 16, 64)
            dropout_rate = trial.suggest_float('dropout_rate', 0.1, 0.5)
            learning_rate = trial.suggest_float('learning_rate', 1e-4, 1e-2, log=True)
            batch_size = trial.suggest_categorical('batch_size', [16, 32, 64])
            time_steps = trial.suggest_int('time_steps', 5, 20)
            
            # For combined models, prepare HMM states
            if model_type.startswith('GMM-HMM'):
                # Train GMM-HMM
                gmm_hmm = SimpleGMMHMM(n_states=n_states)
                gmm_hmm.fit(X_train)
                
                # Get states
                gmm_states_train = gmm_hmm.predict(X_train)
                gmm_states_test = gmm_hmm.predict(X_test)
                
                # Convert to one-hot
                gmm_onehot_train = np.eye(n_states)[gmm_states_train]
                gmm_onehot_test = np.eye(n_states)[gmm_states_test]
                
                # Combine with features
                X_train_hmm = np.hstack((X_train, gmm_onehot_train))
                X_test_hmm = np.hstack((X_test, gmm_onehot_test))
                
            elif model_type.startswith('XGB-HMM'):
                # Train XGB-HMM
                xgb_hmm = SimpleXGBHMM(n_states=n_states)
                xgb_hmm.fit(X_train, y_train)
                
                # Get states
                xgb_states_train = xgb_hmm.predict(X_train)
                xgb_states_test = xgb_hmm.predict(X_test)
                
                # Convert to one-hot
                xgb_onehot_train = np.eye(n_states)[xgb_states_train]
                xgb_onehot_test = np.eye(n_states)[xgb_states_test]
                
                # Combine with features
                X_train_hmm = np.hstack((X_train, xgb_onehot_train))
                X_test_hmm = np.hstack((X_test, xgb_onehot_test))
                
            else:
                # Just use the scaled features for pure LSTM
                X_train_hmm = X_train
                X_test_hmm = X_test
            
            # Create sequences for LSTM
            X_train_seq, y_train_seq = create_sequences(X_train_hmm, y_train, time_steps)
            X_test_seq, y_test_seq = create_sequences(X_test_hmm, y_test, time_steps)
            
            # Skip if we don't have enough samples after creating sequences
            if len(y_train_seq) < batch_size or len(y_test_seq) < 1:
                continue
                
            # Create and train LSTM model
            model = Sequential()
            model.add(LSTM(lstm_units1, input_shape=(time_steps, X_train_hmm.shape[1]), return_sequences=True))
            model.add(Dropout(dropout_rate))
            model.add(LSTM(lstm_units2))
            model.add(Dropout(dropout_rate))
            model.add(Dense(16, activation='relu'))
            model.add(Dense(1, activation='sigmoid'))
            
            model.compile(optimizer=Adam(learning_rate=learning_rate),
                          loss='binary_crossentropy',
                          metrics=['accuracy'])
            
            # Use early stopping to prevent overfitting
            early_stop = EarlyStopping(
                monitor='val_loss',
                patience=10,
                restore_best_weights=True
            )
            
            # Train model with a small validation split
            history = model.fit(
                X_train_seq, y_train_seq,
                epochs=50,
                batch_size=batch_size,
                validation_split=0.2,
                callbacks=[early_stop],
                verbose=0  # Silent training
            )
            
            # Predict on test set
            y_pred_prob = model.predict(X_test_seq, verbose=0)
            y_pred = (y_pred_prob > 0.5).astype(int).flatten()
            
            # Calculate accuracy
            score = accuracy_score(y_test_seq, y_pred)
            
        else:
            # Invalid model type
            score = 0.0
            
        cv_scores.append(score)
    
    # Calculate mean score across all folds
    if cv_scores:
        mean_score = np.mean(cv_scores)
    else:
        mean_score = 0.0
    
    return mean_score

# Create and run the Optuna study
study_name = "tsla_hyperparameter_optimization"
storage_name = "sqlite:///{}.db".format(study_name)

try:
    # Create a new study or load an existing one
    study = optuna.create_study(
        study_name=study_name,
        storage=storage_name,
        load_if_exists=True,
        direction="maximize",
        sampler=TPESampler(seed=42)
    )
    
    # Run optimization
    n_trials = 2  # Adjust based on your computational resources
    study.optimize(objective, n_trials=n_trials)
    
    # Print the best parameters and results
    print("Best trial:")
    trial = study.best_trial
    print("  Value: {}".format(trial.value))
    print("  Params: ")
    for key, value in trial.params.items():
        print("    {}: {}".format(key, value))
    
    # Visualize the optimization results
    try:
        plt.figure(figsize=(12, 8))
        optuna.visualization.matplotlib.plot_optimization_history(study)
        plt.title('Optimization History')
        plt.tight_layout()
        plt.show()
        
        plt.figure(figsize=(12, 8))
        optuna.visualization.matplotlib.plot_param_importances(study)
        plt.title('Parameter Importances')
        plt.tight_layout()
        plt.show()
        
        plt.figure(figsize=(12, 8))
        optuna.visualization.matplotlib.plot_slice(study)
        plt.title('Parameter Relationships')
        plt.tight_layout()
        plt.show()
    except:
        print("Could not generate all visualization plots. Some may require additional dependencies.")
    
    # Train a final model with the best parameters
    print("\nTraining final model with best parameters...")
    
    # Extract the best parameters
    best_params = study.best_params
    
    # Get the best model type
    best_model_type = best_params['model_type']
    print(f"Best model type: {best_model_type}")
    
    # Training details will depend on the best model type
    if best_model_type == 'GMM-HMM':
        print("Implementing the best GMM-HMM model...")
        # Implementation would go here
    elif best_model_type == 'XGB-HMM':
        print("Implementing the best XGB-HMM model...")
        # Implementation would go here
    elif best_model_type.endswith('LSTM'):
        print(f"Implementing the best {best_model_type} model...")
        # Implementation would go here
    
    # Save the study for future reference
    joblib.dump(study, f"{study_name}_study.pkl")
    print(f"Study saved as {study_name}_study.pkl")
    
except Exception as e:
    print(f"Error during hyperparameter optimization: {e}")

/root/vynixmodelling/.venv/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Successfully imported Optuna and other required libraries


[I 2025-08-29 13:15:32,923] Using an existing study with name 'tsla_hyperparameter_optimization' instead of creating a new one.
[I 2025-08-29 13:17:27,654] Trial 72 finished with value: 0.6764285714285715 and parameters: {'volatility_window': 36, 'upper_barrier_multiplier': 0.6475384944386671, 'lower_barrier_multiplier': 1.9229577649232414, 'time_barrier_days': 10, 'use_price_features': False, 'use_ma_features': False, 'use_momentum_features': True, 'use_volatility_features': False, 'use_volume_features': True, 'model_type': 'XGB-HMM+LSTM', 'n_states': 4, 'lstm_units1': 107, 'lstm_units2': 58, 'dropout_rate': 0.4249210561240293, 'learning_rate': 0.009684913368108283, 'batch_size': 16, 'time_steps': 7}. Best is trial 40 with value: 0.7027422303473492.
[I 2025-08-29 13:18:44,318] Trial 73 finished with value: 0.6719141323792487 and parameters: {'volatility_window': 32, 'upper_barrier_multiplier': 0.6354811302834975, 'lower_barrier_multiplier': 1.926733874669873, 'time_barrier_days': 9, '

Best trial:
  Value: 0.7027422303473492
  Params: 
    volatility_window: 14
    upper_barrier_multiplier: 0.5004664285279662
    lower_barrier_multiplier: 1.924443382121896
    time_barrier_days: 16
    use_price_features: True
    use_ma_features: False
    use_momentum_features: True
    use_volatility_features: False
    use_volume_features: True
    model_type: LSTM
    n_states: 3
    lstm_units1: 71
    lstm_units2: 28
    dropout_rate: 0.3485161614734077
    learning_rate: 0.0070666813320739265
    batch_size: 16
    time_steps: 19


<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>


Training final model with best parameters...
Best model type: LSTM
Implementing the best LSTM model...
Study saved as tsla_hyperparameter_optimization_study.pkl


In [19]:
# Implement the best model based on Optuna optimization results
try:
    # Try to load the study if it exists
    best_study = joblib.load(f"{study_name}_study.pkl")
    best_params = best_study.best_params
    print("Loaded best parameters from saved study:")
    for key, value in best_params.items():
        print(f"  {key}: {value}")
    
    # Start with the original dataframe to ensure we have the date column
    print("\nLoading and preparing data with best parameters...")
    original_df = pd.read_csv('dataset/BATS_TSLA, 1D, turnover.csv')
    original_df['date'] = pd.to_datetime(original_df['time'], unit='s')
    
    # Filter data from Jan 1, 2012
    jan_1_2012_timestamp = pd.Timestamp('2012-01-01').timestamp()
    filtered_df_final = original_df[original_df['time'] >= jan_1_2012_timestamp].copy()
    
    # Set date as index for the Triple Barrier Method
    filtered_df_final.set_index('date', inplace=True)
    prices_final = filtered_df_final['close']
    
    # Extract barrier parameters
    best_volatility_window = best_params.get('volatility_window', 20)
    best_upper_barrier = best_params.get('upper_barrier_multiplier', 1.0)
    best_lower_barrier = best_params.get('lower_barrier_multiplier', 1.0)
    best_time_barrier = best_params.get('time_barrier_days', 5)
    
    print(f"\nApplying best Triple Barrier Method parameters:")
    print(f"  Volatility Window: {best_volatility_window}")
    print(f"  Upper Barrier Multiplier: {best_upper_barrier:.2f}")
    print(f"  Lower Barrier Multiplier: {best_lower_barrier:.2f}")
    print(f"  Time Barrier Days: {best_time_barrier}")
    
    optimal_triple_barrier_df = triple_barrier_method(
        prices_final, 
        volatility_window=best_volatility_window, 
        upper_barrier_multiplier=best_upper_barrier,
        lower_barrier_multiplier=best_lower_barrier, 
        time_barrier_days=best_time_barrier
    )
    
    # Feature selection based on best parameters
    print("\nSelecting optimal features...")
    tech_data_final = add_technical_indicators(filtered_df_final.copy())
    tech_data_final = tech_data_final.dropna()
    tech_data_final = tech_data_final.reset_index()  # Reset index to get date as a column
    
    # Select optimal features
    all_features = ['close', 'high', 'low', 'MA5', 'MA20', 'RSI', 
                    'BB_upper', 'BB_lower', 'Volume', 'Histogram', 
                    'MACD', 'Signal', 'K', 'D', 'Turnover (Cr)', 
                    '10 MA Turnover', 'Turnover / 10MA (X)']
    
    optimal_features = []
    
    if best_params.get('use_price_features', True):
        optimal_features.extend(['close', 'high', 'low'])
    if best_params.get('use_ma_features', True):
        optimal_features.extend(['MA5', 'MA20'])
    if best_params.get('use_momentum_features', True):
        optimal_features.extend(['RSI', 'MACD', 'Signal'])
    if best_params.get('use_volatility_features', True):
        optimal_features.extend(['BB_upper', 'BB_lower'])
    if best_params.get('use_volume_features', True):
        optimal_features.extend(['Volume', 'Turnover (Cr)', '10 MA Turnover', 'Turnover / 10MA (X)'])
    
    # Ensure we have at least some features
    if not optimal_features:
        optimal_features = ['close']
    
    # Filter features that exist in the dataframe
    optimal_features = [f for f in optimal_features if f in tech_data_final.columns]
    print(f"Optimal features: {optimal_features}")
    
    # Prepare final dataset
    optimal_triple_barrier_df['start_date'] = pd.to_datetime(optimal_triple_barrier_df['start_date'])
    final_data = pd.merge(tech_data_final, 
                        optimal_triple_barrier_df[['start_date', 'label']], 
                        left_on='date', 
                        right_on='start_date', 
                        how='inner')
    
    # Get features and labels
    X_final = final_data[optimal_features].values
    y_final = (final_data['label'] > 0).astype(int).values
    
    # Scale features
    scaler_final = StandardScaler()
    X_scaled_final = scaler_final.fit_transform(X_final)
    
    # Split into train and test sets
    X_train_final, X_test_final, y_train_final, y_test_final = train_test_split(
        X_scaled_final, y_final, test_size=0.3, shuffle=False
    )
    
    # Best model type
    best_model_type = best_params.get('model_type', 'GMM-HMM')
    best_n_states = best_params.get('n_states', 2)
    
    print(f"\nTraining optimal {best_model_type} model with {best_n_states} states...")
    
    # Train and evaluate the best model
    if best_model_type == 'GMM-HMM':
        # Train optimal GMM-HMM
        optimal_gmm_hmm = SimpleGMMHMM(n_states=best_n_states)
        optimal_gmm_hmm.fit(X_train_final)
        
        # Predict and evaluate
        y_pred_final = optimal_gmm_hmm.predict(X_test_final)
        accuracy_final = accuracy_score(y_test_final, y_pred_final)
        
        print(f"\nOptimal GMM-HMM Accuracy: {accuracy_final:.4f}")
        print("\nClassification Report:")
        print(classification_report(y_test_final, y_pred_final))
        
        # Plot confusion matrix
        plt.figure(figsize=(8, 6))
        cm_final = confusion_matrix(y_test_final, y_pred_final)
        plt.imshow(cm_final, interpolation='nearest', cmap=plt.cm.Blues)
        plt.title('Optimal GMM-HMM Confusion Matrix')
        plt.colorbar()
        tick_marks = np.arange(2)
        plt.xticks(tick_marks, ['Down', 'Up'])
        plt.yticks(tick_marks, ['Down', 'Up'])
        
        # Add text annotations
        thresh = cm_final.max() / 2
        for i in range(cm_final.shape[0]):
            for j in range(cm_final.shape[1]):
                plt.text(j, i, format(cm_final[i, j], 'd'),
                        ha="center", va="center",
                        color="white" if cm_final[i, j] > thresh else "black")
        
        plt.xlabel('Predicted')
        plt.ylabel('True')
        plt.tight_layout()
        plt.show()
        
    elif best_model_type == 'XGB-HMM':
        # Train optimal XGB-HMM
        optimal_xgb_hmm = SimpleXGBHMM(n_states=best_n_states)
        optimal_xgb_hmm.fit(X_train_final, y_train_final)
        
        # Predict and evaluate
        y_pred_final = optimal_xgb_hmm.predict(X_test_final)
        accuracy_final = accuracy_score(y_test_final, y_pred_final)
        
        print(f"\nOptimal XGB-HMM Accuracy: {accuracy_final:.4f}")
        print("\nClassification Report:")
        print(classification_report(y_test_final, y_pred_final))
        
        # Plot confusion matrix
        plt.figure(figsize=(8, 6))
        cm_final = confusion_matrix(y_test_final, y_pred_final)
        plt.imshow(cm_final, interpolation='nearest', cmap=plt.cm.Greens)
        plt.title('Optimal XGB-HMM Confusion Matrix')
        plt.colorbar()
        tick_marks = np.arange(2)
        plt.xticks(tick_marks, ['Down', 'Up'])
        plt.yticks(tick_marks, ['Down', 'Up'])
        
        # Add text annotations
        thresh = cm_final.max() / 2
        for i in range(cm_final.shape[0]):
            for j in range(cm_final.shape[1]):
                plt.text(j, i, format(cm_final[i, j], 'd'),
                        ha="center", va="center",
                        color="white" if cm_final[i, j] > thresh else "black")
        
        plt.xlabel('Predicted')
        plt.ylabel('True')
        plt.tight_layout()
        plt.show()
        
    elif 'LSTM' in best_model_type:
        # Extract LSTM hyperparameters
        best_lstm_units1 = best_params.get('lstm_units1', 64)
        best_lstm_units2 = best_params.get('lstm_units2', 32)
        best_dropout_rate = best_params.get('dropout_rate', 0.2)
        best_learning_rate = best_params.get('learning_rate', 0.001)
        best_batch_size = best_params.get('batch_size', 32)
        best_time_steps = best_params.get('time_steps', 10)
        
        # Prepare data based on model type
        if best_model_type.startswith('GMM-HMM'):
            # Train GMM-HMM
            gmm_hmm_final = SimpleGMMHMM(n_states=best_n_states)
            gmm_hmm_final.fit(X_train_final)
            
            # Get states
            gmm_states_train = gmm_hmm_final.predict(X_train_final)
            gmm_states_test = gmm_hmm_final.predict(X_test_final)
            
            # Convert to one-hot
            gmm_onehot_train = np.eye(best_n_states)[gmm_states_train]
            gmm_onehot_test = np.eye(best_n_states)[gmm_states_test]
            
            # Combine with features
            X_train_hmm = np.hstack((X_train_final, gmm_onehot_train))
            X_test_hmm = np.hstack((X_test_final, gmm_onehot_test))
            
        elif best_model_type.startswith('XGB-HMM'):
            # Train XGB-HMM
            xgb_hmm_final = SimpleXGBHMM(n_states=best_n_states)
            xgb_hmm_final.fit(X_train_final, y_train_final)
            
            # Get states
            xgb_states_train = xgb_hmm_final.predict(X_train_final)
            xgb_states_test = xgb_hmm_final.predict(X_test_final)
            
            # Convert to one-hot
            xgb_onehot_train = np.eye(best_n_states)[xgb_states_train]
            xgb_onehot_test = np.eye(best_n_states)[xgb_states_test]
            
            # Combine with features
            X_train_hmm = np.hstack((X_train_final, xgb_onehot_train))
            X_test_hmm = np.hstack((X_test_final, xgb_onehot_test))
            
        else:
            # Just use the scaled features for pure LSTM
            X_train_hmm = X_train_final
            X_test_hmm = X_test_final
        
        # Create sequences for LSTM
        X_train_seq, y_train_seq = create_sequences(X_train_hmm, y_train_final, best_time_steps)
        X_test_seq, y_test_seq = create_sequences(X_test_hmm, y_test_final, best_time_steps)
        
        # Create optimal LSTM model
        optimal_lstm_model = Sequential()
        optimal_lstm_model.add(LSTM(best_lstm_units1, input_shape=(best_time_steps, X_train_hmm.shape[1]), return_sequences=True))
        optimal_lstm_model.add(Dropout(best_dropout_rate))
        optimal_lstm_model.add(LSTM(best_lstm_units2))
        optimal_lstm_model.add(Dropout(best_dropout_rate))
        optimal_lstm_model.add(Dense(16, activation='relu'))
        optimal_lstm_model.add(Dense(1, activation='sigmoid'))
        
        optimal_lstm_model.compile(optimizer=Adam(learning_rate=best_learning_rate),
                      loss='binary_crossentropy',
                      metrics=['accuracy'])
        
        # Use early stopping
        early_stop = EarlyStopping(
            monitor='val_loss',
            patience=20,
            restore_best_weights=True
        )
        
        # Train the model
        print(f"\nTraining optimal {best_model_type} model...")
        history_final = optimal_lstm_model.fit(
            X_train_seq, y_train_seq,
            epochs=100,
            batch_size=best_batch_size,
            validation_split=0.2,
            callbacks=[early_stop],
            verbose=1
        )
        
        # Predict and evaluate
        y_pred_prob = optimal_lstm_model.predict(X_test_seq)
        y_pred_final = (y_pred_prob > 0.5).astype(int).flatten()
        
        accuracy_final = accuracy_score(y_test_seq, y_pred_final)
        print(f"\nOptimal {best_model_type} Accuracy: {accuracy_final:.4f}")
        print("\nClassification Report:")
        print(classification_report(y_test_seq, y_pred_final))
        
        # Plot training history
        plt.figure(figsize=(10, 6))
        plt.plot(history_final.history['accuracy'], label='Training Accuracy')
        plt.plot(history_final.history['val_accuracy'], label='Validation Accuracy')
        plt.title(f'Optimal {best_model_type} Training')
        plt.xlabel('Epoch')
        plt.ylabel('Accuracy')
        plt.legend()
        plt.tight_layout()
        plt.show()
        
        # Plot confusion matrix
        plt.figure(figsize=(8, 6))
        cm_final = confusion_matrix(y_test_seq, y_pred_final)
        plt.imshow(cm_final, interpolation='nearest', cmap=plt.cm.Blues)
        plt.title(f'Optimal {best_model_type} Confusion Matrix')
        plt.colorbar()
        tick_marks = np.arange(2)
        plt.xticks(tick_marks, ['Down', 'Up'])
        plt.yticks(tick_marks, ['Down', 'Up'])
        
        # Add text annotations
        thresh = cm_final.max() / 2
        for i in range(cm_final.shape[0]):
            for j in range(cm_final.shape[1]):
                plt.text(j, i, format(cm_final[i, j], 'd'),
                        ha="center", va="center",
                        color="white" if cm_final[i, j] > thresh else "black")
        
        plt.xlabel('Predicted')
        plt.ylabel('True')
        plt.tight_layout()
        plt.show()
    
    # Compare with previous best model
    print("\nComparison with previous models:")
    models_comparison = []
    accuracies_comparison = []
    
    # Add previous models if they exist
    try:
        models_comparison.extend(['GMM-HMM', 'XGB-HMM', 'GMM-HMM + LSTM', 'XGB-HMM + LSTM'])
        accuracies_comparison.extend([gmm_accuracy, xgb_hmm_accuracy, gmm_lstm_accuracy, xgb_lstm_accuracy])
    except:
        pass
    
    # Add optimal model
    models_comparison.append(f'Optimal {best_model_type}')
    accuracies_comparison.append(accuracy_final)
    
    # Plot comparison
    plt.figure(figsize=(12, 6))
    colors = ['blue', 'green', 'purple', 'orange', 'red']
    plt.bar(models_comparison, accuracies_comparison, color=colors[:len(models_comparison)])
    plt.ylim(0, 1)
    plt.xlabel('Models')
    plt.ylabel('Accuracy')
    plt.title('Model Accuracy Comparison')
    
    # Add accuracy values on top of bars
    for i, acc in enumerate(accuracies_comparison):
        plt.text(i, acc + 0.02, f'{acc:.4f}', ha='center')
    
    plt.tight_layout()
    plt.show()
    
    # Save the best model
    print(f"\nSaving optimal {best_model_type} model...")
    if 'LSTM' in best_model_type:
        optimal_lstm_model.save(f"optimal_{best_model_type.replace('+', '_plus_')}_model.h5")
        print(f"Model saved as optimal_{best_model_type.replace('+', '_plus_')}_model.h5")
    
except FileNotFoundError:
    print("No saved study found. Please run the hyperparameter optimization cell first.")
except Exception as e:
    print(f"Error implementing the best model: {e}")

Loaded best parameters from saved study:
  volatility_window: 14
  upper_barrier_multiplier: 0.5004664285279662
  lower_barrier_multiplier: 1.924443382121896
  time_barrier_days: 16
  use_price_features: True
  use_ma_features: False
  use_momentum_features: True
  use_volatility_features: False
  use_volume_features: True
  model_type: LSTM
  n_states: 3
  lstm_units1: 71
  lstm_units2: 28
  dropout_rate: 0.3485161614734077
  learning_rate: 0.0070666813320739265
  batch_size: 16
  time_steps: 19

Loading and preparing data with best parameters...

Applying best Triple Barrier Method parameters:
  Volatility Window: 14
  Upper Barrier Multiplier: 0.50
  Lower Barrier Multiplier: 1.92
  Time Barrier Days: 16

Selecting optimal features...
Optimal features: ['close', 'high', 'low', 'RSI', 'MACD', 'Signal', 'Volume', 'Turnover (Cr)', '10 MA Turnover', 'Turnover / 10MA (X)']

Training optimal LSTM model with 3 states...

Training optimal LSTM model...
Epoch 1/100
118/118 ━━━━━━━━━━━━━━━━━━

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>


Comparison with previous models:


<IPython.core.display.Javascript object>


Saving optimal LSTM model...
Model saved as optimal_LSTM_model.h5


In [20]:
# Get the top 3 trials from your study
top_trials = sorted(best_study.trials, key=lambda t: t.value if t.value is not None else float('-inf'), reverse=True)[:10]

print("Top 3 Models from Hyperparameter Optimization:")
for i, trial in enumerate(top_trials):
    print(f"\nModel #{i+1} - Accuracy: {trial.value:.4f}")
    print(f"Model type: {trial.params.get('model_type', 'N/A')}")
    print("Parameters:")
    for key, value in trial.params.items():
        if key != 'model_type':
            print(f"  {key}: {value}")

Top 3 Models from Hyperparameter Optimization:

Model #1 - Accuracy: 0.7027
Model type: LSTM
Parameters:
  volatility_window: 14
  upper_barrier_multiplier: 0.5004664285279662
  lower_barrier_multiplier: 1.924443382121896
  time_barrier_days: 16
  use_price_features: True
  use_ma_features: False
  use_momentum_features: True
  use_volatility_features: False
  use_volume_features: True
  n_states: 3
  lstm_units1: 71
  lstm_units2: 28
  dropout_rate: 0.3485161614734077
  learning_rate: 0.0070666813320739265
  batch_size: 16
  time_steps: 19

Model #2 - Accuracy: 0.6840
Model type: LSTM
Parameters:
  volatility_window: 12
  upper_barrier_multiplier: 0.6165685298261303
  lower_barrier_multiplier: 1.9339705733403865
  time_barrier_days: 12
  use_price_features: False
  use_ma_features: False
  use_momentum_features: True
  use_volatility_features: False
  use_volume_features: True
  n_states: 3
  lstm_units1: 124
  lstm_units2: 63
  dropout_rate: 0.47006661282153095
  learning_rate: 0.003

In [21]:
# Create line chart visualization of actual vs predicted values
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from matplotlib.dates import DateFormatter

# Extract the test dates (if using the optimized LSTM model)
try:
    # Assuming we have the test data and predictions available
    # Get the dates from the test set
    # We need to offset by time_steps since LSTM predictions start after the sequence length
    best_time_steps = best_params.get('time_steps', 19)  # From the best params
    
    # Get the dates from the merged data
    test_dates = final_data.iloc[-len(y_test_seq):]['date'].values
    
    # Create a DataFrame with predictions and actual values
    results_df = pd.DataFrame({
        'Date': pd.to_datetime(test_dates),
        'Actual': y_test_seq,
        'Predicted': y_pred_final,
        'Probability': y_pred_prob.flatten()
    })
    
    # Sort by date
    results_df = results_df.sort_values('Date')
    
    # Plot the results
    plt.figure(figsize=(16, 8))
    
    # Plot actual values
    plt.plot(results_df['Date'], results_df['Actual'], 'b-', label='Actual', linewidth=2)
    
    # Plot predicted values
    plt.plot(results_df['Date'], results_df['Predicted'], 'r-', label='Predicted', linewidth=2)
    
    # Plot prediction probabilities
    plt.plot(results_df['Date'], results_df['Probability'], 'g--', label='Prediction Probability', alpha=0.5)
    
    # Format x-axis to show dates nicely
    plt.gca().xaxis.set_major_formatter(DateFormatter('%Y-%m-%d'))
    plt.gcf().autofmt_xdate()
    
    # Add grid, legend and labels
    plt.grid(True, alpha=0.3)
    plt.legend(loc='best')
    plt.title('Tesla Stock Price Movement Prediction (Actual vs Predicted)', fontsize=16)
    plt.xlabel('Date', fontsize=12)
    plt.ylabel('Movement (1=Up, 0=Down)', fontsize=12)
    
    # Add horizontal lines at 0.5 probability threshold and binary outcomes
    plt.axhline(y=0.5, color='gray', linestyle='--', alpha=0.5, label='Decision Threshold')
    plt.axhline(y=0, color='gray', linestyle='-', alpha=0.2)
    plt.axhline(y=1, color='gray', linestyle='-', alpha=0.2)
    
    plt.tight_layout()
    plt.show()
    
    # Calculate prediction accuracy by month
    results_df['Month'] = results_df['Date'].dt.to_period('M')
    monthly_accuracy = results_df.groupby('Month').apply(
        lambda x: (x['Actual'] == x['Predicted']).mean()
    )
    
    # Plot monthly accuracy
    plt.figure(figsize=(16, 6))
    monthly_accuracy.plot(kind='bar', color='skyblue')
    plt.title('Prediction Accuracy by Month', fontsize=16)
    plt.xlabel('Month', fontsize=12)
    plt.ylabel('Accuracy', fontsize=12)
    plt.axhline(y=accuracy_final, color='red', linestyle='--', label=f'Overall Accuracy: {accuracy_final:.4f}')
    plt.ylim(0, 1)
    plt.legend()
    plt.grid(True, alpha=0.3)
    plt.tight_layout()
    plt.show()
    
    # Plot the actual stock prices with prediction overlay
    try:
        # Get original price data for the test period
        test_price_data = tech_data_final[tech_data_final['date'].isin(results_df['Date'])]
        
        # Create a figure with dual y-axes
        fig, ax1 = plt.subplots(figsize=(16, 8))
        
        # Plot the stock price
        ax1.set_xlabel('Date', fontsize=12)
        ax1.set_ylabel('Stock Price ($)', fontsize=12, color='blue')
        ax1.plot(test_price_data['date'], test_price_data['close'], 'b-', label='Tesla Stock Price')
        ax1.tick_params(axis='y', labelcolor='blue')
        
        # Create a second y-axis for prediction results
        ax2 = ax1.twinx()
        ax2.set_ylabel('Prediction', fontsize=12, color='red')
        
        # Plot the prediction (using step function to show binary predictions clearly)
        ax2.step(results_df['Date'], results_df['Predicted'], 'r-', label='Predicted Movement', where='post', alpha=0.7)
        
        # Add colorized background based on prediction (green for up, red for down)
        for i in range(len(results_df) - 1):
            if results_df['Predicted'].iloc[i] == 1:  # Up prediction
                ax1.axvspan(results_df['Date'].iloc[i], results_df['Date'].iloc[i+1], 
                            alpha=0.2, color='green')
            else:  # Down prediction
                ax1.axvspan(results_df['Date'].iloc[i], results_df['Date'].iloc[i+1], 
                            alpha=0.2, color='red')
                
        # Format x-axis to show dates nicely
        plt.gca().xaxis.set_major_formatter(DateFormatter('%Y-%m-%d'))
        plt.gcf().autofmt_xdate()
        
        # Add legend for both axes
        lines1, labels1 = ax1.get_legend_handles_labels()
        lines2, labels2 = ax2.get_legend_handles_labels()
        ax1.legend(lines1 + lines2, labels1 + labels2, loc='best')
        
        plt.title('Tesla Stock Price with Movement Predictions', fontsize=16)
        plt.grid(True, alpha=0.3)
        plt.tight_layout()
        plt.show()
    
    except Exception as e:
        print(f"Could not create price overlay chart: {e}")

except Exception as e:
    print(f"Error creating visualization: {e}")
    print("Make sure you have run the model optimization and have predictions available.")
    
    # Alternative: Visualize one of the basic models if available
    try:
        # Try to visualize XGB-HMM+LSTM results
        test_dates = pd.to_datetime(tech_data.iloc[-len(xgb_y_test_seq):]['date'].values)
        
        results_df = pd.DataFrame({
            'Date': test_dates,
            'Actual': xgb_y_test_seq,
            'Predicted': xgb_lstm_pred,
        })
        
        plt.figure(figsize=(16, 8))
        plt.plot(results_df['Date'], results_df['Actual'], 'b-', label='Actual', linewidth=2)
        plt.plot(results_df['Date'], results_df['Predicted'], 'r-', label='Predicted', linewidth=2)
        
        plt.gca().xaxis.set_major_formatter(DateFormatter('%Y-%m-%d'))
        plt.gcf().autofmt_xdate()
        
        plt.grid(True, alpha=0.3)
        plt.legend(loc='best')
        plt.title('Tesla Stock Price Movement Prediction (XGB-HMM+LSTM)', fontsize=16)
        plt.xlabel('Date', fontsize=12)
        plt.ylabel('Movement (1=Up, 0=Down)', fontsize=12)
        
        plt.tight_layout()
        plt.show()
    except Exception as e:
        print(f"Could not create alternative visualization: {e}")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Backtesting

In [22]:
!pip install backtrader

In [28]:
import backtrader as bt
import pandas as pd
import numpy as np
import datetime
import os
import sys
import matplotlib.pyplot as plt
from tensorflow.keras.models import load_model
from sklearn.preprocessing import StandardScaler

# Custom Strategy using LSTM-HMM model signals with risk management
class LSTMHMMRiskStrategy(bt.Strategy):
    params = (
        ('model_path', 'optimal_LSTM_model.h5'),  # Path to your trained model
        ('max_risk_pct', 1),  # Maximum risk as percentage of portfolio (0.1%)
        ('risk_reward_ratio', 1.0),  # Risk to reward ratio (1:1)
        ('printlog', True),  # Set to True to enable detailed logging
    )

    def log(self, txt, dt=None, doprint=False):
        """Logging function"""
        if self.params.printlog or doprint:
            dt = dt or self.datas[0].datetime.date(0)
            print(f'{dt.isoformat()}, {txt}')

    def __init__(self):
        # Keep reference to close line
        self.dataclose = self.datas[0].close
        self.datahigh = self.datas[0].high
        self.datalow = self.datas[0].low
        self.datavolume = self.datas[0].volume
        
        # Additional data features for model input
        self.macd = bt.indicators.MACD(self.datas[0])
        self.rsi = bt.indicators.RSI(self.datas[0])
        self.bb = bt.indicators.BollingerBands(self.datas[0], period=20, devfactor=2)
        
        # To track orders
        self.order = None
        self.buyprice = None
        self.buycomm = None
        
        # To track stop loss and take profit levels
        self.stop_loss = None
        self.take_profit = None
        
        # For risk management
        self.max_risk_amount = None
        
        # For performance metrics calculation
        self.daily_returns = []
        self.trade_dates = []
        
        # Load the trained model
        try:
            self.model = load_model(self.params.model_path)
            print(f"Successfully loaded model from {self.params.model_path}")
            # Get the input shape expected by the model
            self.input_shape = self.model.layers[0].input_shape
            print(f"Model expects input shape: {self.input_shape}")
        except Exception as e:
            print(f"Error loading model: {e}")
            # Default to a simple moving average strategy if model loading fails
            self.sma = bt.indicators.SimpleMovingAverage(self.datas[0], period=20)
            self.model = None
        
        # Data for model input preparation
        self.features_buffer = []
        # Set time_steps from model input shape if available, otherwise use default
        self.time_steps = 10  # Default value
        if hasattr(self, 'input_shape') and self.input_shape and len(self.input_shape) > 1:
            self.time_steps = self.input_shape[1]
            print(f"Using time_steps={self.time_steps} from model configuration")
        
        # Initialize the scaler (would be better to load the exact same scaler used during training)
        self.scaler = StandardScaler()
        
        # Dictionary to store signals and performance
        self.signals = {}
        self.trades = []
        
        # For performance metrics
        self.portfolio_value_history = []
        self.dates_history = []

    def notify_order(self, order):
        if order.status in [order.Submitted, order.Accepted]:
            # Order submitted/accepted - no action required
            self.log(f'ORDER {order.Status[order.status]}')
            return

        # Check if an order has been completed
        if order.status in [order.Completed]:
            if order.isbuy():
                self.log(
                    f'BUY EXECUTED, Price: {order.executed.price:.2f}, '
                    f'Cost: {order.executed.value:.2f}, Commission: {order.executed.comm:.2f}'
                )
                self.buyprice = order.executed.price
                self.buycomm = order.executed.comm
                
                # Set stop loss and take profit levels for buy order
                if self.stop_loss is not None and self.take_profit is not None:
                    self.log(f'Setting SL: {self.stop_loss:.2f}, TP: {self.take_profit:.2f}')
            else:  # Sell
                self.log(
                    f'SELL EXECUTED, Price: {order.executed.price:.2f}, '
                    f'Cost: {order.executed.value:.2f}, Commission: {order.executed.comm:.2f}'
                )
                
                # If this was a sell to exit a position, record the trade
                if self.position.size == 0:
                    # Calculate P&L
                    if self.buyprice:
                        pnl = (order.executed.price - self.buyprice) * order.executed.size - self.buycomm - order.executed.comm
                        pnl_pct = (pnl / (self.buyprice * order.executed.size)) * 100
                        self.trades.append({
                            'entry_price': self.buyprice,
                            'exit_price': order.executed.price,
                            'size': order.executed.size,
                            'pnl': pnl,
                            'pnl_pct': pnl_pct,
                            'exit_date': self.datas[0].datetime.date(0)
                        })
                        self.log(f'TRADE COMPLETED, PnL: ${pnl:.2f} ({pnl_pct:.2f}%)')

            # Reset stop loss and take profit after order execution
            if self.position.size == 0:
                self.stop_loss = None
                self.take_profit = None

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            self.log(f'Order {order.Status[order.status]}')

        # Reset order
        self.order = None

    def notify_trade(self, trade):
        if not trade.isclosed:
            return

        self.log(f'OPERATION PROFIT, GROSS {trade.pnl:.2f}, NET {trade.pnlcomm:.2f}')

    def prepare_features(self):
        """Prepare features for model input"""
        # Extract current features
        features = {
            'close': self.dataclose[0],
            'high': self.datahigh[0],
            'low': self.datalow[0],
            'RSI': self.rsi[0],
            'MACD': self.macd.macd[0],
            'Signal': self.macd.signal[0],
            'Volume': self.datavolume[0],
            'BB_upper': self.bb.top[0],
            'BB_lower': self.bb.bot[0],
            'Turnover (Cr)': self.datavolume[0] * self.dataclose[0] / 10000000,  # Approximate
        }
        
        # Calculate '10 MA Turnover'
        if len(self) >= 10:
            ma_turnover = sum([self.datavolume[-i] * self.dataclose[-i] for i in range(10)]) / 10 / 10000000
            features['10 MA Turnover'] = ma_turnover
            
            # Calculate 'Turnover / 10MA (X)'
            if ma_turnover > 0:
                features['Turnover / 10MA (X)'] = features['Turnover (Cr)'] / ma_turnover
            else:
                features['Turnover / 10MA (X)'] = 1.0
        else:
            features['10 MA Turnover'] = features['Turnover (Cr)']
            features['Turnover / 10MA (X)'] = 1.0
        
        # Add to buffer
        self.features_buffer.append(features)
        
        # Keep only the last time_steps entries
        if len(self.features_buffer) > self.time_steps:
            self.features_buffer.pop(0)
            
        return self.features_buffer

    def calculate_position_size(self, stop_loss_price):
        """Calculate position size based on risk management rules"""
        # Current portfolio value
        portfolio_value = self.broker.getvalue()
        
        # Maximum amount we're willing to risk (0.1% of portfolio)
        max_risk_amount = portfolio_value * (self.params.max_risk_pct / 100.0)
        
        # Risk per share
        price = self.dataclose[0]
        risk_per_share = abs(price - stop_loss_price)
        
        # Calculate position size
        if risk_per_share > 0:
            position_size = max_risk_amount / risk_per_share
            # Round down to nearest whole number
            position_size = int(position_size)
            
            # Ensure minimum position size of 1
            position_size = max(1, position_size)
            
            return position_size
        else:
            return 1  # Default to 1 if risk calculation fails

    def get_model_prediction(self):
        """Get prediction from the model"""
        if len(self.features_buffer) < self.time_steps:
            # Not enough data yet
            return None
            
        if self.model is None:
            # No model loaded, use simple MA logic instead
            if self.dataclose[0] > self.sma[0]:
                return 1  # Buy signal
            elif self.dataclose[0] < self.sma[0]:
                return 0  # Sell signal
            return None
            
        try:
            # Convert buffer to features array
            # Use only 10 features that match the model's expected input
            feature_names = ['close', 'high', 'low', 'RSI', 'MACD', 'Signal', 'Volume',
                           'BB_upper', 'BB_lower', 'Turnover (Cr)']
            
            # Extract only the features we need in the correct order
            features_array = np.array([[buffer_item.get(feature, 0) for feature in feature_names] 
                                      for buffer_item in self.features_buffer])
            
            # Fit scaler on this batch and transform (ideally we'd use the same scaler as during training)
            if len(features_array) >= self.time_steps:
                features_scaled = self.scaler.fit_transform(features_array)
                
                # Reshape for LSTM input [samples, time_steps, features]
                X = features_scaled.reshape(1, self.time_steps, len(feature_names))
                
                # Get prediction
                prediction = self.model.predict(X, verbose=0)[0][0]
                
                # Store the prediction for this date
                dt = self.datas[0].datetime.date(0)
                self.signals[dt] = prediction
                
                # Return binary signal (threshold at 0.5)
                signal = 1 if prediction > 0.5 else 0
                self.log(f"MODEL PREDICTION: {prediction:.4f} -> Signal: {'BUY' if signal == 1 else 'SELL'}")
                return signal
        except Exception as e:
            self.log(f"Error in prediction: {e}")
            
        return None

    def next(self):
        # Update the maximum risk amount
        self.max_risk_amount = self.broker.getvalue() * (self.params.max_risk_pct / 100.0)
        
        # Store portfolio value for performance metrics
        current_date = self.datas[0].datetime.date(0)
        self.portfolio_value_history.append(self.broker.getvalue())
        self.dates_history.append(current_date)
        
        # Calculate daily return
        if len(self.portfolio_value_history) >= 2:
            daily_return = (self.portfolio_value_history[-1] / self.portfolio_value_history[-2]) - 1
            self.daily_returns.append(daily_return)
            self.trade_dates.append(current_date)
        
        # Log the closing price
        self.log(f'Close: {self.dataclose[0]:.2f}, High: {self.datahigh[0]:.2f}, Low: {self.datalow[0]:.2f}')

        # Check for stop loss or take profit
        if self.position.size > 0 and self.stop_loss is not None and self.take_profit is not None:
            # Check if price hit stop loss
            if self.datalow[0] <= self.stop_loss:
                self.log(f'STOP LOSS TRIGGERED at {self.stop_loss:.2f}')
                self.order = self.sell(exectype=bt.Order.Market)
                return
            
            # Check if price hit take profit
            if self.datahigh[0] >= self.take_profit:
                self.log(f'TAKE PROFIT TRIGGERED at {self.take_profit:.2f}')
                self.order = self.sell(exectype=bt.Order.Market)
                return

        # Check if an order is pending
        if self.order:
            return

        # Prepare features and get model prediction
        self.prepare_features()
        signal = self.get_model_prediction()
        
        if signal is None:
            # Not enough data yet or error in prediction
            self.log("No signal generated (insufficient data or error)")
            return
            
        # Check if we are in the market
        if not self.position:
            # We are not in the market, look for a buy signal
            if signal == 1:
                # Calculate stop loss level (using ATR or fixed percentage)
                # For simplicity, we'll use a fixed 2% below current price
                sl_pct = 0.02  # 2% stop loss
                self.stop_loss = self.dataclose[0] * (1 - sl_pct)
                
                # Calculate take profit based on R:R ratio
                tp_pct = sl_pct * self.params.risk_reward_ratio
                self.take_profit = self.dataclose[0] * (1 + tp_pct)
                
                # Calculate position size based on risk management
                size = self.calculate_position_size(self.stop_loss)
                
                self.log(f'BUY CREATE, {self.dataclose[0]:.2f}, Size: {size}, SL: {self.stop_loss:.2f}, TP: {self.take_profit:.2f}')
                
                # Keep track of the created order to avoid a 2nd order
                self.order = self.buy(size=size)
        else:
            # We are in the market, look for a sell signal
            if signal == 0:
                self.log(f'SELL CREATE, {self.dataclose[0]:.2f}')
                # Keep track of the created order to avoid a 2nd order
                self.order = self.sell()

    def stop(self):
        # Calculate final portfolio value and return
        final_value = self.broker.getvalue()
        initial_value = 1000000.0
        profit_loss = final_value - initial_value
        percent_return = (profit_loss / initial_value) * 100
        
        # Log performance metrics
        self.log(f'Final Portfolio Value: ${final_value:.2f}', doprint=True)
        self.log(f'Profit/Loss: ${profit_loss:.2f} ({percent_return:.2f}%)', doprint=True)
        
        # Calculate trade statistics
        if self.trades:
            num_trades = len(self.trades)
            winning_trades = sum(1 for trade in self.trades if trade['pnl'] > 0)
            losing_trades = sum(1 for trade in self.trades if trade['pnl'] <= 0)
            win_rate = (winning_trades / num_trades) * 100 if num_trades > 0 else 0
            
            avg_profit = np.mean([trade['pnl'] for trade in self.trades if trade['pnl'] > 0]) if winning_trades > 0 else 0
            avg_loss = np.mean([trade['pnl'] for trade in self.trades if trade['pnl'] <= 0]) if losing_trades > 0 else 0
            
            self.log(f'Total Trades: {num_trades}', doprint=True)
            self.log(f'Win Rate: {win_rate:.2f}%', doprint=True)
            self.log(f'Average Profit: ${avg_profit:.2f}', doprint=True)
            self.log(f'Average Loss: ${avg_loss:.2f}', doprint=True)
            
            # Calculate max drawdown
            if num_trades > 0:
                equity_curve = [initial_value]
                for trade in self.trades:
                    equity_curve.append(equity_curve[-1] + trade['pnl'])
                
                max_equity = initial_value
                max_drawdown = 0
                
                for equity in equity_curve:
                    max_equity = max(max_equity, equity)
                    drawdown = (max_equity - equity) / max_equity * 100
                    max_drawdown = max(max_drawdown, drawdown)
                
                self.log(f'Max Drawdown: {max_drawdown:.2f}%', doprint=True)
        
        # Calculate Sharpe Ratio and Sortino Ratio
        if len(self.daily_returns) > 1:
            # Annualized return
            total_days = len(self.daily_returns)
            annual_factor = 252  # Trading days in a year
            avg_daily_return = np.mean(self.daily_returns)
            annual_return = ((1 + avg_daily_return) ** annual_factor) - 1
            
            # Standard deviation of returns (for Sharpe)
            daily_std = np.std(self.daily_returns)
            annual_std = daily_std * np.sqrt(annual_factor)
            
            # Downside deviation (for Sortino)
            negative_returns = [ret for ret in self.daily_returns if ret < 0]
            downside_std = np.std(negative_returns) if negative_returns else 0
            annual_downside_std = downside_std * np.sqrt(annual_factor)
            
            # Calculate Sharpe Ratio (assuming risk-free rate of 0% for simplicity)
            sharpe_ratio = annual_return / annual_std if annual_std > 0 else 0
            
            # Calculate Sortino Ratio
            sortino_ratio = annual_return / annual_downside_std if annual_downside_std > 0 else 0
            
            self.log(f'Sharpe Ratio: {sharpe_ratio:.4f}', doprint=True)
            self.log(f'Sortino Ratio: {sortino_ratio:.4f}', doprint=True)
            self.log(f'Annualized Return: {annual_return:.2f}%', doprint=True)
            self.log(f'Annualized Volatility: {annual_std:.2f}%', doprint=True)
        
        # Save signals to CSV
        if hasattr(self, 'signals') and len(self.signals) > 0:
            signals_df = pd.DataFrame.from_dict(self.signals, orient='index', columns=['Probability'])
            signals_df.index.name = 'Date'
            signals_df.to_csv('model_signals.csv')
            self.log('Saved model signals to model_signals.csv', doprint=True)
            
        # Save trade history to CSV
        if self.trades:
            trades_df = pd.DataFrame(self.trades)
            trades_df.to_csv('trade_history.csv')
            self.log('Saved trade history to trade_history.csv', doprint=True)
            
        # Save performance metrics to CSV
        if len(self.daily_returns) > 0:
            performance_df = pd.DataFrame({
                'Date': self.trade_dates,
                'Portfolio_Value': self.portfolio_value_history[1:],  # Align with dates
                'Daily_Return': self.daily_returns
            })
            performance_df.to_csv('performance_metrics.csv', index=False)
            self.log('Saved performance metrics to performance_metrics.csv', doprint=True)


# First, prepare the data
# Read the CSV file
print("Loading data...")
df = pd.read_csv('dataset/TSLA_from_2012.csv')

# Convert time to datetime
df['date'] = pd.to_datetime(df['time'], unit='s')

# Format the data for backtrader
data_for_bt = df[['date', 'open', 'high', 'low', 'close', 'Volume']].copy()
data_for_bt.columns = ['datetime', 'open', 'high', 'low', 'close', 'volume']  # Rename columns for backtrader
data_for_bt = data_for_bt.set_index('datetime')

# Save the processed data to a temporary CSV that backtrader can use
temp_csv_path = 'temp_backtest_data.csv'
data_for_bt.to_csv(temp_csv_path, date_format='%Y-%m-%d')
print(f"Prepared data saved to {temp_csv_path}")

if __name__ == '__main__':
    # Create a cerebro entity
    cerebro = bt.Cerebro()

    # Add a strategy
    cerebro.addstrategy(LSTMHMMRiskStrategy, printlog=True)  # Explicitly enable logging

    # Load the data into a pandas dataframe
    dataframe = pd.read_csv(temp_csv_path, index_col=0, parse_dates=True)
    
    # Define test period (30% of the data, similar to train/test split)
    total_days = len(dataframe)
    test_start_idx = int(total_days * 0.7)  # 70/30 train/test split
    
    # Get the date corresponding to the test start
    if test_start_idx < total_days:
        test_start_date = dataframe.index[test_start_idx]
        print(f"Using test data starting from {test_start_date}")
    else:
        test_start_date = dataframe.index[0]
        print("Warning: Using all data as test data")
    
    # Create a Data Feed (only using test data)
    from backtrader.feeds import PandasData
    
    class MyPandasData(PandasData):
        """Custom PandasData class with specific parameters"""
        params = (
            ('datetime', None),  # Column for date (index in our case)
            ('open', 'open'),    # Column for open price
            ('high', 'high'),    # Column for high price 
            ('low', 'low'),      # Column for low price
            ('close', 'close'),  # Column for close price
            ('volume', 'volume'),# Column for volume
            ('openinterest', None),  # No open interest data
        )
    
    # Filter for test data only
    test_dataframe = dataframe.loc[test_start_date:]
    
    # Create the data feed
    data = MyPandasData(dataname=test_dataframe)

    # Add the Data Feed to Cerebro
    cerebro.adddata(data)

    # Set our desired cash start
    cerebro.broker.setcash(1000000.0)

    # Set the commission - 0.1% per transaction
    cerebro.broker.setcommission(commission=0.001)

    # Print out the starting conditions
    print('Starting Portfolio Value: %.2f' % cerebro.broker.getvalue())

    # Run over everything
    cerebro.run(stdstats=True)

    # Plot the result
    cerebro.plot(style='candlestick', barup='green', bardown='red',
                 plotdist=0.1, volume=True, fmt_x_data='%Y-%m-%d')

Loading data...
Prepared data saved to temp_backtest_data.csv
Using test data starting from 2021-07-22 00:00:00
Starting Portfolio Value: 1000000.00


Successfully loaded model from optimal_LSTM_model.h5
Error loading model: 'LSTM' object has no attribute 'input_shape'
2021-09-08, Close: 251.29, High: 254.82, Low: 246.92
2021-09-08, No signal generated (insufficient data or error)
2021-09-09, Close: 251.62, High: 254.03, Low: 250.54
2021-09-09, No signal generated (insufficient data or error)
2021-09-10, Close: 245.42, High: 254.20, Low: 244.84
2021-09-10, No signal generated (insufficient data or error)
2021-09-13, Close: 247.67, High: 248.26, Low: 236.28
2021-09-13, No signal generated (insufficient data or error)
2021-09-14, Close: 248.16, High: 251.49, Low: 245.47
2021-09-14, No signal generated (insufficient data or error)
2021-09-15, Close: 251.94, High: 252.29, Low: 246.12
2021-09-15, No signal generated (insufficient data or error)
2021-09-16, Close: 252.33, High: 252.97, Low: 249.20
2021-09-16, No signal generated (insufficient data or error)
2021-09-17, Close: 253.16, High: 253.68, Low: 250.00
2021-09-17, No signal generate

<IPython.core.display.Javascript object>

# Building Deep Reinforcement Learning

# Deep Reinforcement Learning Trading Agent

This implementation combines:
1. **LSTM Feature Extractor**: Uses the pre-trained LSTM model to extract temporal features from market data
2. **DRL Agents**: PPO (Proximal Policy Optimization) and SAC (Soft Actor-Critic) for trading decisions
3. **Custom Trading Environment**: OpenAI Gym-compatible environment for training and testing

The architecture leverages the LSTM's ability to capture temporal patterns while allowing the DRL agent to learn optimal trading policies through interaction with the market environment.

In [2]:
!pip install gym stable-baselines3[extra]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/721.7 kB ? eta -:--:--  Downloading gym-0.26.2.tar.gz (721 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 721.7/721.7 kB 21.2 MB/s  0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 721.7/721.7 kB 21.2 MB/s  0:00:00
  Installing build dependencies ...   Installing build dependencies ... -done
  Getting requirements to build wheel ... one
  Getting requirements to build wheel ... -done
  Preparing metadata (pyproject.toml) ... one
  Preparing metadata (pyproject.toml) ... -done
one
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 944.3/944.3 kB 39.3 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/887.9 MB ? eta -:--:--Downloading gymnasium-1.2.0-py3-none-any.whl (944 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 944.3/944.3 kB 39.3 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 887.9/887.9 MB 50.4 MB/s  0:00:11m0:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 887.9/887.9 MB 50.4 MB/s  0:00:11
   ━━━━━

In [3]:
import gym
from gym import spaces
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.models import load_model
import tensorflow as tf
from stable_baselines3 import PPO, SAC
from stable_baselines3.common.env_util import make_vec_env
from stable_baselines3.common.callbacks import EvalCallback, StopTrainingOnRewardThreshold
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.results_plotter import load_results, ts2xy
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore')

class TradingEnvironment(gym.Env):
    """
    Custom Trading Environment that uses LSTM as feature extractor
    """
    
    def __init__(self, df, lstm_model_path, initial_balance=100000, 
                 transaction_cost=0.001, time_steps=10, max_position=1.0):
        super(TradingEnvironment, self).__init__()
        
        self.df = df.reset_index(drop=True)
        self.initial_balance = initial_balance
        self.transaction_cost = transaction_cost
        self.time_steps = time_steps
        self.max_position = max_position
        
        # Load LSTM model for feature extraction
        try:
            self.lstm_model = load_model(lstm_model_path)
            print(f"Loaded LSTM model from {lstm_model_path}")
        except:
            print("Warning: Could not load LSTM model, using random features")
            self.lstm_model = None
        
        # Initialize scalers
        self.price_scaler = StandardScaler()
        self.feature_scaler = StandardScaler()
        
        # Prepare features
        self._prepare_features()
        
        # Define action and observation spaces
        # Actions: 0=Hold, 1=Buy, 2=Sell (continuous action for position size)
        self.action_space = spaces.Box(low=-1.0, high=1.0, shape=(1,), dtype=np.float32)
        
        # Observation space: LSTM features + market state + portfolio state
        lstm_features = 32 if self.lstm_model else 10  # Adjust based on LSTM output
        market_features = 5  # price, volume, volatility, trend, etc.
        portfolio_features = 3  # balance, position, unrealized_pnl
        obs_size = lstm_features + market_features + portfolio_features
        
        self.observation_space = spaces.Box(
            low=-np.inf, high=np.inf, 
            shape=(obs_size,), dtype=np.float32
        )
        
        # Initialize environment state
        self.reset()
    
    def _prepare_features(self):
        """Prepare features for LSTM and environment"""
        # Calculate technical indicators
        self.df['returns'] = self.df['close'].pct_change()
        self.df['volatility'] = self.df['returns'].rolling(20).std()
        self.df['sma_20'] = self.df['close'].rolling(20).mean()
        self.df['rsi'] = self._calculate_rsi(self.df['close'])
        self.df['macd'] = self._calculate_macd(self.df['close'])
        
        # Fill NaN values
        self.df = self.df.fillna(method='bfill').fillna(method='ffill')
        
        # Scale features for LSTM
        feature_cols = ['open', 'high', 'low', 'close', 'volume', 
                       'returns', 'volatility', 'sma_20', 'rsi', 'macd']
        
        if len(self.df) > 0:
            self.feature_scaler.fit(self.df[feature_cols].values)
    
    def _calculate_rsi(self, prices, period=14):
        """Calculate RSI indicator"""
        delta = prices.diff()
        gain = (delta.where(delta > 0, 0)).rolling(window=period).mean()
        loss = (-delta.where(delta < 0, 0)).rolling(window=period).mean()
        rs = gain / loss
        return 100 - (100 / (1 + rs))
    
    def _calculate_macd(self, prices, fast=12, slow=26):
        """Calculate MACD indicator"""
        exp1 = prices.ewm(span=fast).mean()
        exp2 = prices.ewm(span=slow).mean()
        return exp1 - exp2
    
    def _extract_lstm_features(self, current_idx):
        """Extract features using LSTM model"""
        if self.lstm_model is None:
            # Return random features if LSTM model not available
            return np.random.randn(32).astype(np.float32)
        
        if current_idx < self.time_steps:
            # Not enough data for LSTM, return zeros
            return np.zeros(32, dtype=np.float32)
        
        # Get time series data
        start_idx = max(0, current_idx - self.time_steps)
        end_idx = current_idx
        
        feature_cols = ['open', 'high', 'low', 'close', 'volume', 
                       'returns', 'volatility', 'sma_20', 'rsi', 'macd']
        
        time_series_data = self.df.iloc[start_idx:end_idx][feature_cols].values
        
        if len(time_series_data) < self.time_steps:
            # Pad with zeros if not enough data
            padding = np.zeros((self.time_steps - len(time_series_data), len(feature_cols)))
            time_series_data = np.vstack([padding, time_series_data])
        
        # Scale the data
        time_series_scaled = self.feature_scaler.transform(time_series_data)
        
        # Reshape for LSTM input
        lstm_input = time_series_scaled.reshape(1, self.time_steps, len(feature_cols))
        
        try:
            # Get LSTM features (assume LSTM outputs features, not predictions)
            # If your LSTM outputs predictions, you might need to extract intermediate layers
            lstm_features = self.lstm_model.predict(lstm_input, verbose=0)[0]
            
            # If LSTM outputs a single value, expand to feature vector
            if len(lstm_features.shape) == 0:
                lstm_features = np.array([lstm_features])
            
            # Ensure we have the right number of features
            if len(lstm_features) != 32:
                # Pad or truncate to 32 features
                if len(lstm_features) < 32:
                    lstm_features = np.pad(lstm_features, (0, 32 - len(lstm_features)))
                else:
                    lstm_features = lstm_features[:32]
            
            return lstm_features.astype(np.float32)
        
        except Exception as e:
            print(f"Error in LSTM feature extraction: {e}")
            return np.zeros(32, dtype=np.float32)
    
    def _get_observation(self):
        """Get current observation"""
        if self.current_step >= len(self.df):
            # Return zeros if we're at the end
            return np.zeros(self.observation_space.shape[0], dtype=np.float32)
        
        # Get LSTM features
        lstm_features = self._extract_lstm_features(self.current_step)
        
        # Get market features
        current_data = self.df.iloc[self.current_step]
        market_features = np.array([
            current_data['close'] / 1000,  # Normalized price
            current_data['volume'] / 1000000,  # Normalized volume
            current_data['volatility'] * 100,  # Volatility percentage
            current_data['rsi'] / 100,  # Normalized RSI
            current_data['returns'] * 100  # Returns percentage
        ], dtype=np.float32)
        
        # Get portfolio features
        portfolio_features = np.array([
            self.balance / self.initial_balance,  # Normalized balance
            self.position,  # Current position
            self.unrealized_pnl / self.initial_balance  # Normalized unrealized P&L
        ], dtype=np.float32)
        
        # Combine all features
        observation = np.concatenate([
            lstm_features,
            market_features,
            portfolio_features
        ])
        
        return observation
    
    def reset(self):
        """Reset the environment"""
        self.current_step = self.time_steps  # Start after we have enough data for LSTM
        self.balance = self.initial_balance
        self.position = 0.0  # Current position (-1 to 1)
        self.entry_price = 0.0
        self.unrealized_pnl = 0.0
        self.total_reward = 0.0
        self.trade_count = 0
        self.episode_trades = []
        
        return self._get_observation()
    
    def step(self, action):
        """Execute one step in the environment"""
        if self.current_step >= len(self.df) - 1:
            # End of data
            return self._get_observation(), 0, True, {}
        
        # Get current price
        current_price = self.df.iloc[self.current_step]['close']
        
        # Interpret action
        action_value = np.clip(action[0], -1.0, 1.0)
        target_position = action_value * self.max_position
        
        # Calculate position change
        position_change = target_position - self.position
        
        # Calculate reward
        reward = self._calculate_reward(current_price, position_change)
        
        # Execute trade if position changes
        if abs(position_change) > 0.01:  # Minimum trade threshold
            self._execute_trade(current_price, position_change)
        
        # Update unrealized P&L
        if self.position != 0:
            self.unrealized_pnl = (current_price - self.entry_price) * self.position * 1000  # Position size multiplier
        else:
            self.unrealized_pnl = 0
        
        # Move to next step
        self.current_step += 1
        
        # Check if done
        done = (self.current_step >= len(self.df) - 1) or (self.balance <= 0)
        
        # Additional info
        info = {
            'balance': self.balance,
            'position': self.position,
            'unrealized_pnl': self.unrealized_pnl,
            'total_trades': self.trade_count,
            'current_price': current_price
        }
        
        self.total_reward += reward
        
        return self._get_observation(), reward, done, info
    
    def _calculate_reward(self, current_price, position_change):
        """Calculate reward for the current action"""
        # Price change reward
        if self.current_step > 0:
            previous_price = self.df.iloc[self.current_step - 1]['close']
            price_change = (current_price - previous_price) / previous_price
            
            # Reward for correct position during price movements
            position_reward = self.position * price_change * 1000
        else:
            position_reward = 0
        
        # Transaction cost penalty
        transaction_penalty = abs(position_change) * self.transaction_cost * current_price * 100
        
        # Risk penalty for large positions
        risk_penalty = abs(self.position) * 0.01
        
        # Reward for realized profits
        realized_reward = 0
        if abs(position_change) > 0.01 and self.position != 0:
            if (self.position > 0 and position_change < 0) or (self.position < 0 and position_change > 0):
                # Closing position
                profit = (current_price - self.entry_price) * min(abs(self.position), abs(position_change))
                realized_reward = profit / self.initial_balance * 1000
        
        total_reward = position_reward - transaction_penalty - risk_penalty + realized_reward
        
        return total_reward
    
    def _execute_trade(self, price, position_change):
        """Execute a trade"""
        trade_value = abs(position_change) * price
        transaction_cost = trade_value * self.transaction_cost
        
        # Update balance
        if position_change > 0:  # Buying
            if self.balance >= trade_value + transaction_cost:
                self.balance -= (trade_value + transaction_cost)
                if self.position == 0:
                    self.entry_price = price
                else:
                    # Update weighted average entry price
                    total_position = self.position + position_change
                    if total_position != 0:
                        self.entry_price = (self.entry_price * self.position + price * position_change) / total_position
                
                self.position += position_change
                self.trade_count += 1
                
                self.episode_trades.append({
                    'step': self.current_step,
                    'action': 'BUY',
                    'price': price,
                    'size': position_change,
                    'balance': self.balance
                })
        
        else:  # Selling
            if position_change < 0:  # Selling
                # Always allow selling (can go short)
                self.balance += (trade_value - transaction_cost)
                
                if self.position != 0:
                    # Calculate realized P&L
                    realized_pnl = (price - self.entry_price) * min(abs(position_change), abs(self.position))
                    
                    if abs(self.position + position_change) < 0.01:
                        # Closing position
                        self.position = 0
                        self.entry_price = 0
                    else:
                        self.position += position_change
                        if self.position * (self.position + position_change) < 0:
                            # Changed direction, update entry price
                            self.entry_price = price
                else:
                    # Opening short position
                    self.position += position_change
                    self.entry_price = price
                
                self.trade_count += 1
                
                self.episode_trades.append({
                    'step': self.current_step,
                    'action': 'SELL',
                    'price': price,
                    'size': abs(position_change),
                    'balance': self.balance
                })

# DRL Agent Wrapper Class
class DRLTradingAgent:
    """
    Deep Reinforcement Learning Trading Agent
    Supports both PPO and SAC algorithms
    """
    
    def __init__(self, env, algorithm='PPO', policy='MlpPolicy', **kwargs):
        self.env = env
        self.algorithm = algorithm
        self.policy = policy
        
        # Create the model
        if algorithm == 'PPO':
            self.model = PPO(
                policy=policy,
                env=env,
                learning_rate=kwargs.get('learning_rate', 3e-4),
                n_steps=kwargs.get('n_steps', 2048),
                batch_size=kwargs.get('batch_size', 64),
                n_epochs=kwargs.get('n_epochs', 10),
                gamma=kwargs.get('gamma', 0.99),
                clip_range=kwargs.get('clip_range', 0.2),
                ent_coef=kwargs.get('ent_coef', 0.01),
                verbose=1
            )
        elif algorithm == 'SAC':
            self.model = SAC(
                policy=policy,
                env=env,
                learning_rate=kwargs.get('learning_rate', 3e-4),
                buffer_size=kwargs.get('buffer_size', 1000000),
                batch_size=kwargs.get('batch_size', 256),
                tau=kwargs.get('tau', 0.005),
                gamma=kwargs.get('gamma', 0.99),
                ent_coef=kwargs.get('ent_coef', 'auto'),
                verbose=1
            )
        else:
            raise ValueError(f"Unsupported algorithm: {algorithm}")
    
    def train(self, total_timesteps=100000, eval_freq=5000, eval_episodes=10):
        """Train the DRL agent"""
        print(f"Training {self.algorithm} agent for {total_timesteps} timesteps...")
        
        # Create evaluation callback
        eval_callback = EvalCallback(
            self.env, 
            best_model_save_path=f"./best_{self.algorithm.lower()}_model",
            log_path=f"./logs_{self.algorithm.lower()}/",
            eval_freq=eval_freq,
            n_eval_episodes=eval_episodes,
            deterministic=True,
            render=False
        )
        
        # Train the model
        self.model.learn(
            total_timesteps=total_timesteps,
            callback=eval_callback
        )
        
        print(f"Training completed!")
        return self.model
    
    def test(self, test_episodes=10, render=False):
        """Test the trained agent"""
        print(f"Testing {self.algorithm} agent for {test_episodes} episodes...")
        
        episode_rewards = []
        episode_infos = []
        
        for episode in range(test_episodes):
            obs = self.env.reset()
            episode_reward = 0
            episode_trades = []
            done = False
            
            while not done:
                action, _states = self.model.predict(obs, deterministic=True)
                obs, reward, done, info = self.env.step(action)
                episode_reward += reward
                
                if 'current_price' in info:
                    episode_trades.append({
                        'reward': reward,
                        'balance': info['balance'],
                        'position': info['position'],
                        'price': info['current_price']
                    })
            
            episode_rewards.append(episode_reward)
            episode_infos.append({
                'episode': episode + 1,
                'total_reward': episode_reward,
                'final_balance': info['balance'],
                'total_trades': info['total_trades'],
                'trades': episode_trades
            })
            
            print(f"Episode {episode + 1}: Reward = {episode_reward:.2f}, "
                  f"Final Balance = {info['balance']:.2f}, Trades = {info['total_trades']}")
        
        avg_reward = np.mean(episode_rewards)
        std_reward = np.std(episode_rewards)
        
        print(f"\nTest Results:")
        print(f"Average Reward: {avg_reward:.2f} ± {std_reward:.2f}")
        print(f"Best Episode Reward: {max(episode_rewards):.2f}")
        print(f"Worst Episode Reward: {min(episode_rewards):.2f}")
        
        return episode_rewards, episode_infos
    
    def save_model(self, path):
        """Save the trained model"""
        self.model.save(path)
        print(f"Model saved to {path}")
    
    def load_model(self, path):
        """Load a trained model"""
        if self.algorithm == 'PPO':
            self.model = PPO.load(path)
        elif self.algorithm == 'SAC':
            self.model = SAC.load(path)
        print(f"Model loaded from {path}")

# Usage Example
def create_and_train_drl_agent(df, lstm_model_path, algorithm='PPO'):
    """
    Create and train a DRL trading agent
    """
    print(f"Creating trading environment...")
    
    # Create environment
    env = TradingEnvironment(
        df=df,
        lstm_model_path=lstm_model_path,
        initial_balance=100000,
        transaction_cost=0.001,
        time_steps=10,
        max_position=1.0
    )
    
    print(f"Environment created with observation space: {env.observation_space.shape}")
    print(f"Action space: {env.action_space.shape}")
    
    # Create DRL agent
    agent = DRLTradingAgent(
        env=env,
        algorithm=algorithm,
        learning_rate=3e-4,
        gamma=0.99
    )
    
    # Train the agent
    trained_model = agent.train(total_timesteps=50000, eval_freq=2500)
    
    # Test the agent
    episode_rewards, episode_infos = agent.test(test_episodes=5)
    
    # Save the model
    agent.save_model(f"drl_{algorithm.lower()}_trading_model")
    
    return agent, episode_rewards, episode_infos

print("DRL Trading System with LSTM Feature Extractor is ready!")
print("Available components:")
print("- TradingEnvironment: Custom Gym environment with LSTM features")
print("- DRLTradingAgent: Wrapper for PPO/SAC algorithms")
print("- create_and_train_drl_agent: Function to create and train agents")
print("\nTo use:")
print("agent, rewards, infos = create_and_train_drl_agent(df, 'optimal_LSTM_model.h5', 'PPO')")

Gym has been unmaintained since 2022 and does not support NumPy 2.0 amongst other critical functionality.
Please upgrade to Gymnasium, the maintained drop-in replacement of Gym, or contact the authors of your software and request that they upgrade.
Users of this version of Gym should be able to simply replace 'import gym' with 'import gymnasium as gym' in the vast majority of cases.
See the migration guide at https://gymnasium.farama.org/introduction/migration_guide/ for additional information.
2025-08-30 04:30:05.311047: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-08-30 04:30:05.311047: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical opera

DRL Trading System with LSTM Feature Extractor is ready!
Available components:
- TradingEnvironment: Custom Gym environment with LSTM features
- DRLTradingAgent: Wrapper for PPO/SAC algorithms
- create_and_train_drl_agent: Function to create and train agents

To use:
agent, rewards, infos = create_and_train_drl_agent(df, 'optimal_LSTM_model.h5', 'PPO')


In [6]:
pip install stable-baselines3[extra] gym

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [10]:
pip install shimmy>=2.0

Note: you may need to restart the kernel to use updated packages.


In [ ]:
# Train and Compare PPO and SAC Agents
print("=" * 60)
print("TRAINING DRL AGENTS WITH LSTM FEATURE EXTRACTOR")
print("=" * 60)

# Load the data (reuse the processed data from earlier)
try:
    df_drl = pd.read_csv('temp_backtest_data.csv', index_col=0, parse_dates=True)
    print(f"Loaded data with {len(df_drl)} rows")
    
    # Reset index to make it easier to work with
    df_drl = df_drl.reset_index()
    df_drl.columns = ['date', 'open', 'high', 'low', 'close', 'volume']
    
    # Use a subset of data for faster training (last 2000 days)
    df_train = df_drl.tail(2000).reset_index(drop=True)
    print(f"Using {len(df_train)} days for training")
    
    # Train PPO Agent
    print("\n" + "=" * 40)
    print("TRAINING PPO AGENT")
    print("=" * 40)
    
    ppo_agent, ppo_rewards, ppo_infos = create_and_train_drl_agent(
        df=df_train,
        lstm_model_path='optimal_LSTM_model.h5',
        algorithm='PPO'
    )
    
    # Train SAC Agent
    print("\n" + "=" * 40)
    print("TRAINING SAC AGENT")
    print("=" * 40)
    
    sac_agent, sac_rewards, sac_infos = create_and_train_drl_agent(
        df=df_train,
        lstm_model_path='optimal_LSTM_model.h5',
        algorithm='SAC'
    )
    
    # Compare Results
    print("\n" + "=" * 50)
    print("COMPARING RESULTS")
    print("=" * 50)
    
    ppo_avg = np.mean(ppo_rewards)
    ppo_std = np.std(ppo_rewards)
    sac_avg = np.mean(sac_rewards)
    sac_std = np.std(sac_rewards)
    
    print(f"PPO Agent Results:")
    print(f"  Average Reward: {ppo_avg:.2f} ± {ppo_std:.2f}")
    print(f"  Best Episode: {max(ppo_rewards):.2f}")
    
    print(f"\nSAC Agent Results:")
    print(f"  Average Reward: {sac_avg:.2f} ± {sac_std:.2f}")
    print(f"  Best Episode: {max(sac_rewards):.2f}")
    
    if ppo_avg > sac_avg:
        print(f"\n🏆 PPO performs better by {ppo_avg - sac_avg:.2f} average reward")
    else:
        print(f"\n🏆 SAC performs better by {sac_avg - ppo_avg:.2f} average reward")
    
    # Plot comparison
    plt.figure(figsize=(12, 6))
    
    plt.subplot(1, 2, 1)
    plt.bar(['PPO', 'SAC'], [ppo_avg, sac_avg], 
            yerr=[ppo_std, sac_std], capsize=5)
    plt.title('Average Reward Comparison')
    plt.ylabel('Average Reward')
    
    plt.subplot(1, 2, 2)
    episodes = range(1, len(ppo_rewards) + 1)
    plt.plot(episodes, ppo_rewards, 'b-o', label='PPO', alpha=0.7)
    plt.plot(episodes, sac_rewards, 'r-s', label='SAC', alpha=0.7)
    plt.title('Episode Rewards')
    plt.xlabel('Episode')
    plt.ylabel('Reward')
    plt.legend()
    plt.grid(True, alpha=0.3)
    
    plt.tight_layout()
    plt.show()
    
    # Detailed performance analysis
    print("\n" + "=" * 50)
    print("DETAILED PERFORMANCE ANALYSIS")
    print("=" * 50)
    
    for i, (algo, infos) in enumerate([('PPO', ppo_infos), ('SAC', sac_infos)]):
        print(f"\n{algo} Agent Analysis:")
        final_balances = [info['final_balance'] for info in infos]
        total_trades = [info['total_trades'] for info in infos]
        
        print(f"  Average Final Balance: ${np.mean(final_balances):.2f}")
        print(f"  Balance Std Dev: ${np.std(final_balances):.2f}")
        print(f"  Average Trades per Episode: {np.mean(total_trades):.1f}")
        print(f"  Profit Episodes: {sum(1 for b in final_balances if b > 100000)}/{len(final_balances)}")
        
        roi = [(b - 100000) / 100000 * 100 for b in final_balances]
        print(f"  Average ROI: {np.mean(roi):.2f}%")
        print(f"  Best ROI: {max(roi):.2f}%")
        print(f"  Worst ROI: {min(roi):.2f}%")

except Exception as e:
    print(f"Error in DRL training: {e}")
    print("This might be due to missing dependencies. Install them with:")
    print("pip install stable-baselines3[extra] gym")
    
    # Alternative: Create a simple demo environment
    print("\nCreating demo environment for testing...")
    
    # Create sample data
    np.random.seed(42)
    dates = pd.date_range('2020-01-01', periods=1000, freq='D')
    prices = 100 * np.exp(np.cumsum(np.random.randn(1000) * 0.02))
    
    demo_df = pd.DataFrame({
        'date': dates,
        'open': prices * (1 + np.random.randn(1000) * 0.001),
        'high': prices * (1 + np.abs(np.random.randn(1000)) * 0.01),
        'low': prices * (1 - np.abs(np.random.randn(1000)) * 0.01),
        'close': prices,
        'volume': np.random.randint(1000000, 10000000, 1000)
    })
    
    print(f"Created demo dataset with {len(demo_df)} rows")
    print("Shape:", demo_df.shape)
    print("Columns:", demo_df.columns.tolist())
    print("Price range: ${:.2f} - ${:.2f}".format(demo_df['close'].min(), demo_df['close'].max()))

TRAINING DRL AGENTS WITH LSTM FEATURE EXTRACTOR
Loaded data with 3434 rows
Using 2000 days for training

TRAINING PPO AGENT
Creating trading environment...
Loaded LSTM model from optimal_LSTM_model.h5
Environment created with observation space: (40,)
Action space: (1,)
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Environment created with observation space: (40,)
Action space: (1,)
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Training PPO agent for 50000 timesteps...
Training PPO agent for 50000 timesteps...
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.99e+03 |
|    ep_rew_mean     | -4e+04   |
| time/              |          |
|    fps             | 14       |
|    iterations      | 1        |
|    time_elapsed    | 139      |
|    total_timesteps | 2048     |
---------------------------------
---------------------------------
| rollout/     

In [8]:
# Install Required Dependencies (run this first if needed)
import subprocess
import sys

def install_requirements():
    """Install required packages for DRL trading"""
    requirements = [
        'stable-baselines3[extra]',
        'gym==0.21.0',  # Compatible version
        'matplotlib',
        'numpy',
        'pandas',
        'scikit-learn',
        'tensorflow'
    ]
    
    print("Installing required packages...")
    for package in requirements:
        try:
            print(f"Installing {package}...")
            subprocess.check_call([sys.executable, "-m", "pip", "install", package])
            print(f"✅ {package} installed successfully")
        except subprocess.CalledProcessError as e:
            print(f"❌ Error installing {package}: {e}")
        except Exception as e:
            print(f"❌ Unexpected error with {package}: {e}")
    
    print("Installation complete!")

# Uncomment the line below to install dependencies
# install_requirements()

# Test imports
try:
    import gym
    import stable_baselines3
    from stable_baselines3 import PPO, SAC
    print("✅ All DRL dependencies are available!")
    print(f"Gym version: {gym.__version__}")
    print(f"Stable Baselines3 version: {stable_baselines3.__version__}")
    
except ImportError as e:
    print(f"❌ Missing dependency: {e}")
    print("Please run: install_requirements()")
    print("Or manually install with: pip install stable-baselines3[extra] gym==0.21.0")

✅ All DRL dependencies are available!
Gym version: 0.26.2
Stable Baselines3 version: 2.7.0
